## 第5章: 係り受け解析

夏目漱石の小説『吾輩は猫である』の文章（neko.txt）をCaboChaを使って係り受け解析し，その結果をneko.txt.cabochaというファイルに保存せよ．このファイルを用いて，以下の問に対応するプログラムを実装せよ．



## 40. 係り受け解析結果の読み込み（形態素）(×)
形態素を表すクラスMorphを実装せよ．このクラスは表層形（surface），基本形（base），品詞（pos），品詞細分類1（pos1）をメンバ変数に持つこととする．さらに，CaboChaの解析結果（neko.txt.cabocha）を読み込み，各文をMorphオブジェクトのリストとして表現し，3文目の形態素列を表示せよ．




In [1]:
class Morph:
    def __init__(self, surface, base, pos, pos1):
        self.surface = surface
        self.base = base
        self.pos = pos
        self.pos1 = pos1
        
    def __str__(self):
        '''オブジェクトの文字列表現'''
        return 'surface[{}]\tbase[{}]\tpos[{}]\tpos1[{}]'\
            .format(self.surface, self.base, self.pos, self.pos1)

        
def neco_lines():
    with open("./neko.txt.cabocha") as file_parsed:
        morphs = []
        for line in file_parsed:
            # 1文の終了判定
            if line == 'EOS\n':
                yield morphs
                morphs = []
            else:
                # 先頭が*の行は係り受け解析結果なのでスキップ
                if line[0] == '*':
                    continue
                # 表層形はtab区切り、それ以外は','区切りでバラす
                cols = line.split('\t')
                res_cols = cols[1].split(',')

                # Morph作成、リストに追加
                morphs.append(Morph(
                    cols[0],        # surface
                    res_cols[6],    # base
                    res_cols[0],    # pos
                    res_cols[1]     # pos1
                ))

        raise StopIteration

In [2]:

# 1文ずつリスト作成
for i, morphs in enumerate(neco_lines()):
    # 3文目を表示
    if i == 3:
        for morph in morphs:
            print(morph)
        break

surface[名前]	base[名前]	pos[名詞]	pos1[一般]
surface[は]	base[は]	pos[助詞]	pos1[係助詞]
surface[まだ]	base[まだ]	pos[副詞]	pos1[助詞類接続]
surface[無い]	base[無い]	pos[形容詞]	pos1[自立]
surface[。]	base[。]	pos[記号]	pos1[句点]


## 41. 係り受け解析結果の読み込み（文節・係り受け）(×)
40に加えて，文節を表すクラスChunkを実装せよ．  
このクラスは形態素（Morphオブジェクト）のリスト（morphs），係り先文節インデックス番号（dst），係り元文節インデックス番号のリスト（srcs）をメンバ変数に持つこととする．  
さらに，入力テキストのCaboChaの解析結果を読み込み，１文をChunkオブジェクトのリストとして表現し，8文目の文節の文字列と係り先を表示せよ．第5章の残りの問題では，ここで作ったプログラムを活用せよ．

In [101]:
"""
係り受け情報　'* 1 2D 0/1 -0.764522\n'
    カラム	意味
    1	先頭カラムは*。係り受け解析結果であることを示す。
    2	文節番号（0から始まる整数）
    3	係り先番号＋D
    4	主辞/機能語の位置と任意の個数の素性列
    5	係り関係のスコア。係りやすさの度合で、一般に大きな値ほど係りやすい。
        
形態素情報　　'吾輩\t名詞,代名詞,一般,*,*,*,吾輩,ワガハイ,ワガハイ\n'

ex:
* 0 5D 0/1 -1.514009
吾輩	名詞,代名詞,一般,*,*,*,吾輩,ワガハイ,ワガハイ
は	助詞,係助詞,*,*,*,*,は,ハ,ワ
* 1 2D 0/1 1.311423
ここ	名詞,代名詞,一般,*,*,*,ここ,ココ,ココ
で	助詞,格助詞,一般,*,*,*,で,デ,デ
* 2 3D 0/1 0.123057
始め	動詞,自立,*,*,一段,連用形,始める,ハジメ,ハジメ
て	助詞,接続助詞,*,*,*,*,て,テ,テ
* 3 4D 0/1 1.440044
人間	名詞,一般,*,*,*,*,人間,ニンゲン,ニンゲン
という	助詞,格助詞,連語,*,*,*,という,トイウ,トユウ
* 4 5D 0/1 -1.514009
もの	名詞,非自立,一般,*,*,*,もの,モノ,モノ
を	助詞,格助詞,一般,*,*,*,を,ヲ,ヲ
* 5 -1D 0/1 0.000000
見	動詞,自立,*,*,一段,連用形,見る,ミ,ミ
た	助動詞,*,*,*,特殊・タ,基本形,た,タ,タ
。	記号,句点,*,*,*,*,。,。,。
EOS          
"""

import re
class Chunk:
    def __init__(self):
        """
        形態素（Morphオブジェクト）のリスト（morphs)
        係り先文節インデックス番号（dst）
        係り元文節インデックス番号のリスト（srcs）
        """
        self.morphs = []
        self.dst = []
        self.srcs = []
    
    def __str__(self):
        '''オブジェクトの文字列表現'''
        surface = ''
        for morph in self.morphs:
            surface += morph.surface
        return '{}\tsrcs{}\tdst[{}]'.format(surface, self.srcs, self.dst)
    
    def print_chunk(self):
        surface = ''
        for morph in self.morphs:
            if morph.pos != "記号":
                surface += morph.surface
        return surface
    
    def pos_list(self):
        return [morph.pos for morph in self.morphs]
    


def neco_lines():
    with open("./neko.txt.cabocha") as file_parsed:
        chunks = dict()     # idxをkeyにChunkを格納
        idx = -1
        for line in file_parsed:
            # 1文の終了判定
            if line == 'EOS\n':
                # Chunkのリストを返す
                if len(chunks) > 0:
                    # chunksをkeyでソートし、valueのみ取り出し
                    sorted_tuple = sorted(chunks.items(), key=lambda x: x[0])
                    yield list(zip(*sorted_tuple))[1]
                    chunks.clear()
                else:
                    yield []

            # 先頭が*の行は係り受け解析結果なので、Chunkを作成
            elif line[0] == '*':

                # Chunkのインデックス番号と係り先のインデックス番号取得
                cols = line.split(' ')
                idx = int(cols[1])
                dst = int(re.search(r'(.*?)D', cols[2]).group(1))

                # Chunkを生成（なければ）し、係り先のインデックス番号セット
                if idx not in chunks:
                    chunks[idx] = Chunk()
                chunks[idx].dst = dst

                # 係り先のChunkを生成（なければ）し、係り元インデックス番号追加
                if dst != -1:
                    if dst not in chunks:
                        chunks[dst] = Chunk()
                    chunks[dst].srcs.append(idx)

            
            # それ以外の行は形態素解析結果なので、Morphを作りChunkに追加
            else:
                # 表層形はtab区切り、それ以外は','区切りでバラす
                cols = line.split('\t')
                res_cols = cols[1].split(',')

                # Morph作成、リストに追加
                chunks[idx].morphs.append(
                    Morph(
                        cols[0],        # surface
                        res_cols[6],    # base
                        res_cols[0],    # pos
                        res_cols[1]     # pos1
                    )
                )

        raise StopIteration

    
# 1文ずつリスト作成
for i, chunks in enumerate(neco_lines(), 1):
    # 8文目を表示
    if i ==3:
        for j, chunk in enumerate(chunks):
            print('[{}]{}'.format(j, chunk))
        break
    
        
    

[0]　	srcs[]	dst[2]
[1]吾輩は	srcs[]	dst[2]
[2]猫である。	srcs[0, 1]	dst[-1]


## 42. 係り元と係り先の文節の表示

係り元の文節と係り先の文節のテキストをタブ区切り形式ですべて抽出せよ．ただし，句読点などの記号は出力しないようにせよ．

In [50]:
for i, chunks in enumerate(neco_lines(), 1):
    for j, chunk in enumerate(chunks):
        if chunk.dst != -1:
            print('{}\t{}'.format(chunk.print_chunk(),chunks[chunk.dst].print_chunk()))

	猫である
吾輩は	猫である
名前は	無い
まだ	無い
どこで	生れたか
生れたか	つかぬ
とんと	つかぬ
見当が	つかぬ
何でも	薄暗い
薄暗い	所で
じめじめした	所で
所で	泣いて
ニャーニャー	泣いて
泣いて	記憶している
いた事だけは	記憶している
吾輩は	見た
ここで	始めて
始めて	人間という
人間という	ものを
ものを	見た
しかも	種族であったそうだ
あとで	聞くと
聞くと	種族であったそうだ
それは	種族であったそうだ
書生という	人間中で
人間中で	種族であったそうだ
一番	獰悪な
獰悪な	種族であったそうだ
この	書生というのは
書生というのは	話である
時々	捕えて
我々を	捕えて
捕えて	煮て
煮て	食うという
食うという	話である
しかし	思わなかった
その	当時は
当時は	なかったから
何という	考も
考も	なかったから
なかったから	思わなかった
別段	恐し
恐し	思わなかった
いとも	思わなかった
ただ	載せられて
彼の	掌に
掌に	載せられて
載せられて	持ち上げられた
スーと	持ち上げられた
持ち上げられた	時
時	フワフワした
何だか	フワフワした
フワフワした	感じが
感じが	あったばかりである
掌の	上で
上で	落ちついて
少し	落ちついて
落ちついて	見たのが
書生の	顔を
顔を	見たのが
見たのが	人間という
いわゆる	人間という
人間という	ものの
ものの	見始であろう
この	時
時	ものだと
妙な	ものだと
ものだと	思った
思った	感じが
感じが	残っている
今でも	残っている
第一毛をもって	装飾されべきはずの
装飾されべきはずの	顔が
顔が	つるつるして
つるつるして	薬缶だ
まるで	薬缶だ
その後	逢ったが
猫にも	逢ったが
だいぶ	逢ったが
逢ったが	ない
こんな	片輪には
片輪には	ない
一度も	出会わした
出会わした	事が
事が	ない
のみならず	突起している
顔の	真中が
真中が	突起している
あまりに	突起している
そうして	吹く
その穴の	中から
中から	吹く
時々	吹く
ぷうぷうと煙を	吹く
どうも	咽せぽくて
咽せぽくて	弱った
実に	弱った
これが	ものである
人間の	飲む
飲む	煙草という
煙草という	ものである
ものである	事は
事は	知った
ようやく	知った
この	頃
頃	知った


心臓は	おった
たしかに	おった
平時よりも	烈しく
烈しく	鼓動して
鼓動して	おった
彼は	猫だ
大に	軽蔑せる
軽蔑せる	調子で
調子で	猫だ
何	猫だ
	あ
猫が	聞いて
聞いて	あ
あきれら	あ
全てえ	住んでるんだ
どこに	住んでるんだ
住んでるんだ	傍若無人である
随分	傍若無人である
吾輩は	いるのだ
ここの	教師の
教師の	家に
家に	いるのだ
いるのだ	事だろうと
どうせ	事だろうと
そんな	事だろうと
事だろうと	思った
いやに	瘠せてるじゃねえかと
瘠せてるじゃねえかと	吹きかける
大王だけに	吹きかける
気焔を	吹きかける
言葉付から	察すると
察すると	思われない
どうも	思われない
良家の	猫とも
猫とも	思われない
しかし	暮しているらしい
その	膏
膏	切って
切って	肥満している
肥満している	ところを
ところを	見ると
見ると	食ってるらしい
御馳走を	食ってるらしい
食ってるらしい	暮しているらしい
豊かに	暮しているらしい
吾輩は	聞かざるを得なかった
そう	誰だいと
云う君は	誰だいと
一体	誰だいと
誰だいと	聞かざるを得なかった
己れあ	黒よ昂然たる
車屋の	黒よ昂然たる
黒よ昂然たる	ものだ
車屋の	黒は
黒は	乱暴猫である
この	近辺で
近辺で	知らぬ
知らぬ	者
者	乱暴猫である
なき	乱暴猫である
しかし	交際しない
車屋だけに	強いばかりで
強いばかりで	ないから
ちっとも	ないから
教育が	ないから
ないから	交際しない
あまり	交際しない
誰も	交際しない
同盟敬遠主義の	的に
的に	なっている
なっている	奴だ
吾輩は	起すと同時に
彼の	名を
名を	聞いて
聞いて	起すと同時に
少々	こそばゆき
尻	こそばゆき
こそばゆき	感じを
感じを	起すと同時に
起すと同時に	生じたのである
一方では	生じたのである
少々	生じたのである
軽侮の	念も
念も	生じたのである
吾輩は	見た
まず	試してみようと
彼が	無学であるかを
どの	くらい
くらい	無学であるかを
無学であるかを	試してみようと
試してみようと	思って
思って	見た
左の	問答を
問答を	して
して	見た
一体車屋と	教師とは
教師とは	えらいだろう
どっちが	えらいだろう
車屋の	方が
方が	強いに
強いに	いらあな
極って	いらあな
御

第二年目だから	すましているのでも
大方熊の	画だろうなどと
画だろうなどと	知れぬ
気の	知れぬ
知れぬ	ことを
ことを	いって
いって	すましているのでも
すましているのでも	わかる
	持って来た
吾輩が	考えていると
主人の	膝の
膝の	上で
上で	ねむりながら
眼を	ねむりながら
ねむりながら	考えていると
かく	考えていると
考えていると	持って来た
やがて	持って来た
下女が	持って来た
第二の	絵端書を
絵端書を	持って来た
見ると	している
活版で	行列して
舶来の	猫が
猫が	行列して
四五疋ずらりと	行列して
行列して	している
ペンを	握ったり
握ったり	開いたり
書物を	開いたり
開いたり	している
勉強を	している
その	内の
内の	一疋は
一疋は	躍っている
席を	離れて
離れて	躍っている
机の	角で
角で	躍っている
西洋の	猫じゃ
猫じゃ	躍っている
猫じゃを	躍っている
その上に	認められてある
日本の	墨で
墨で	かいて
吾輩は	猫であると
猫であると	黒と
黒と	かいて
かいて	認められてある
右の	側に
側に	読むや
書を	読むや
読むや	認められてある
躍るや	猫の
猫の	春一日という
春一日という	俳句さえ
俳句さえ	認められてある
これは	来たので
主人の	旧門下生より
旧門下生より	来たので
来たので	見たって
誰が	見たって
見たって	一見して
一見して	わかるはずであるのに
意味が	わかるはずであるのに
わかるはずであるのに	悟らないと
迂	主人は
濶な	主人は
主人は	悟らないと
まだ	悟らないと
悟らないと	見えて
見えて	捻って
不思議そうに	捻って
首を	捻って
捻って	言った
はてな	言った
今年は	言った
猫の	年かなと
年かなと	言った
独言を	言った
吾輩が	有名になったのを
これほど	有名になったのを
有名になったのを	着かずに
未だ	着かずに
気が	着かずに
着かずに	いると
いると	見える
ところへ	持ってくる
下女が	持ってくる
また	持ってくる
第三の	端書を
端書を	持ってくる
今度は	絵端書ではない
恭賀新年と	かいて
かいて	ある
傍らに	ある
乍恐縮かの	猫へも
猫へも	ある
宜しく	奉
御伝声	奉
奉	願上候と
願上候と	ある
いかに	迂遠な
迂遠な	主人でも
主人でも	あれば

利かない	ものは
ものは	利かないのだ
無暗に	攻撃する
タカジヤスターゼを	攻撃する
独りで	しているようだ
喧嘩を	しているようだ
今朝の	肝癪が
肝癪が	出す
ちょっと	出す
ここへ	出す
尾を	出す
人間の	日記の
日記の	本色は
本色は	存するのかも知れない
こう	存するのかも知れない
云う辺に	存するのかも知れない
せんだっては	廃すると
朝飯を	廃すると
廃すると	なると
胃が	なると
よく	なると
なると	云うたから
云うたから	見たが
二三日	やめて
朝飯を	やめて
やめて	見たが
見たが	ない
腹が	ぐうぐう鳴るばかりで
ぐうぐう鳴るばかりで	ない
功能は	ない
は	忠告した
是非香の物を	断てと
断てと	忠告した
彼の	説に
説に	よると
よると	ある
すべて	ある
胃病の	源因は
源因は	ある
漬物に	ある
漬物さえ	断てば
断てば	涸らす訳だから
胃病の	源を
源を	涸らす訳だから
涸らす訳だから	疑なしという
本復は	疑なしという
疑なしという	論法であった
それから	触れなかったが
一週間ばかり	触れなかったが
香の物に	触れなかったが
箸を	触れなかったが
触れなかったが	食い出した
別段の	験も
験も	見えなかったから
見えなかったから	食い出した
近頃は	食い出した
また	食い出した
に	聞くと
聞くと	限る
それは	限る
按腹揉療治に	限る
ただし	ゆかぬ
普通のでは	ゆかぬ
皆川流という	揉み方で
古流な	揉み方で
揉み方で	やらせれば
一二度	やらせれば
やらせれば	根治出来る
大抵の	胃病は
胃病は	根治出来る
安井息軒も	愛していた
大変	愛していた
この	按摩術を
按摩術を	愛していた
坂本竜馬のような	豪傑でも
豪傑でも	うけたと
時々は	うけたと
治療を	うけたと
うけたと	云うから
云うから	見た
早速	出掛けて
上根岸まで	出掛けて
出掛けて	揉まして
揉まして	見た
ところが	やる
骨を	揉まなければ
揉まなければ	顛倒しなければ
癒らぬとか	顛倒しなければ
臓腑の	位置を
位置を	顛倒しなければ
一度	顛倒しなければ
顛倒しなければ	いって
根治が	しにくいとか
しにくいとか	いって
いって	やる
それは	やる
それは	やる
残酷な	揉み方を
揉み方を	やる
後で	したので
身体が	したので
綿のようになっ

全体	何という
何という	ものですか
ものですか	あれ
	ものよ
あれは	ものよ
何とかって	ものよ
御師匠さんは	大好きなの
あれが	大好きなの
御師匠さんは	六十二よ
あれで	六十二よ
随分	丈夫だわね
丈夫だわね	六十二で
六十二で	生きている
生きている	くらいだから
くらいだから	なるまい
丈夫と	云わねば
云わねば	なるまい
吾輩は	した
はあと	した
返事を	した
少し	抜けたようだが
間が	抜けたようだが
抜けたようだが	出て来なかったから
別に	出て来なかったから
名答も	出て来なかったから
出て来なかったから	ない
仕方が	ない
あれでも	好かったんだって
もとは	好かったんだって
身分が	好かったんだって
大変	好かったんだって
いつでも	おっしゃるの
そう	おっしゃるの
おっしゃるの	何だったんです
へえ元は	何だったんです
何だったんです	娘なんだって
何でも	行った
天璋院様の	御祐筆の
御祐筆の	妹の
妹の	御嫁に
御嫁に	行った
行った	先きの御っ
先きの御っ	かさんの
かさんの	甥の
甥の	娘なんだって
娘なんだって	すって
何で	すって
	いった
あの	天璋院様の
天璋院様の	御祐筆の
御祐筆の	妹の
妹の	御嫁に
御嫁に	いった
いった	なるほど
少し	待って下さい
天璋院様の	妹の
妹の	御祐筆の
御祐筆の	妹の
あらそうじゃないの	妹の
天璋院様の	御祐筆の
御祐筆の	妹の
妹の	天璋院様のでしょう
よろしい	分りました
分りました	天璋院様のでしょう
天璋院様のでしょう	ええ
ええ	御祐筆のでしょう
御祐筆のでしょう	そうよ
そうよ	行った
御嫁に	行った
行った	行ったですよ
妹の	御嫁に
御嫁に	行ったですよ
行ったですよ	間違った
そう	間違った
そう	間違った
妹の	御嫁に
御嫁に	入った
入った	先きの
先きの	娘なんですとさ
御っ	娘なんですとさ
かさんの	甥の
甥の	娘なんですとさ
娘なんですとさ	娘なんですか
御っ	娘なんですか
かさんの	甥の
甥の	娘なんですか
娘なんですか	ええ
分ったでしょう	いいえ
何だか	混雑して
混雑して	得ないですよ
要領を	得ないですよ
詰る	ところ
ところ	なるんですか
天璋院様の	何に
何に	なるんですか
なるんですか	分らないのね
あなたも	分らないのね
よっぽど	分

...

私は	泣きました
最後の	干を
甘	干を
干を	食っても
食っても	泣きました
まだ	暮れないのを
日が	暮れないのを
暮れないのを	見て
見て	泣きました
然として	泣きました
思わず	泣きました
東風君	泣いたよ
僕は	泣いたよ
実に	情けなくって
情けなくって	泣いたよ
そうだろう	多情多恨だから
芸術家は	多情多恨だから
本来	多情多恨だから
多情多恨だから	同情するが
泣いた	事には
事には	同情するが
同情するが	ものだねと
話は	ものだねと
もっと	早く
早く	進行させたい
進行させたい	ものだねと
ものだねと	いいから
東風君は	いいから
人が	いいから
いいから	している
どこまでも	真面目で
真面目で	滑稽な
滑稽な	挨拶を
挨拶を	している
進行させたいのは	山々だが
山々だが	困るのさ
どうしても	暮れてくれない
日が	暮れてくれない
暮れてくれない	ものだから
ものだから	困るのさ
そう	暮れなくちゃ
日が	暮れなくちゃ
暮れなくちゃ	聞く
聞く	方も
方も	困るから
困るから	やめようと
やめようと	し切れなくなったと
主人が	し切れなくなったと
とうとう	し切れなくなったと
我慢が	し切れなくなったと
し切れなくなったと	見えて
見えて	云い出した
やめちゃ	困ります
なお	困ります
これからが	入る
いよいよ	入る
佳境に	入る
入る	ところですから
それじゃ	聞くから
聞くから	よかろう
早く	暮れた
日が	暮れた
暮れた	事に
事に	したら
したら	よかろう
では	ご注文ですが
少し	ご無理な
ご無理な	ご注文ですが
ご注文ですが	致しましょう
先生の	事ですから
事ですから	枉げて
枉げて	致しましょう
ここは	致しましょう
日が	暮れた
暮れた	事に
事に	致しましょう
それは	好都合だと
好都合だと	澄まして
独仙君が	澄まして
澄まして	述べられたので
述べられたので	噴き出した
一同は	噴き出した
思わず	噴き出した
どっと	噴き出した
いよいよ	入ったので
夜に	入ったので
入ったので	出ました
まず	安心と
安心と	一息ついて
ほっと	一息ついて
一息ついて	出ました
鞍	懸
懸	下宿を
村の	下宿を
下宿を	出ました
私は	嫌ですから
性来騒々しい	所が
所が	嫌ですから
嫌ですから	結んでいたのです
わざと	便利

諸先生が	御まぜ返しになっては
御まぜ返しになっては	至りだが
はなはだ	至りだが
遺憾の	至りだが
至りだが	ない
東風君	一人を
一人を	するより
相手に	するより
するより	ない
致し方が	ない
——	いいかね
いいかね	出たがまた
東風君	二三歩
二三歩	出たがまた
出たがまた	引き返して
引き返して	被ってね
国を	出る
出る	とき
とき	買った
三円二十銭で	買った
買った	赤毛布を
赤毛布を	被ってね
頭から	被ってね
被ってね	判然しなくなった
ふっと	消すと
ランプを	消すと
消すと	判然しなくなった
君	なって
真暗闇に	なって
なって	判然しなくなった
今度は	判然しなくなった
草履の	所在地が
所在地が	判然しなくなった
一体	行くんだい
どこへ	行くんだい
まあ	聞いてたまい
ようやくの	事草履を
事草履を	見つけて
見つけて	出ると
表へ	出ると
出ると	柿落葉
星月夜に	柿落葉
柿落葉	ヴァイオリン
赤毛布に	ヴァイオリン
右へ	右へと
右へと	差しかかってくると
爪先上りに	差しかかってくると
庚申山へ	差しかかってくると
差しかかってくると	響き渡った
東嶺寺の	鐘が
鐘が	響き渡った
ボーンと	毛布を通して
毛布を通して	響き渡った
耳を通して	響き渡った
頭の	中へ
中へ	響き渡った
何時だと	思う
思う	君
これから	云う
秋の	夜長を
夜長を	云う
たった	一人
一人	八丁を
山道	八丁を
八丁を	云う
大平と	云う
云う	所まで
所まで	登るのだが
登るのだが	もので
平生なら	事だから
臆病な	僕の
僕の	事だから
事だから	ところだけれども
恐し	くって
くって	たまらない
たまらない	ところだけれども
ところだけれども	もので
一心不乱と	なると
なると	もので
不思議な	もので
もので	起らないよ
怖いにも	怖くないにも
怖くないにも	起らないよ
毛頭	起らないよ
そんな	念は
念は	起らないよ
てんで	起らないよ
心の	中に
中に	起らないよ
ただ	弾きたいばかりで
ヴァイオリンが	弾きたいばかりで
弾きたいばかりで	なってるんだから
胸が	なってるんだから
一杯に	なってるんだから
なってるんだから	ものさ
妙な	ものさ
この	大平と
大平と	云う
云う	所は
所は	見ると
庚申山の	南側で
南側で	登って
天

まあさ	議論だから
議論だから	聞いていろ
だまって	聞いていろ
どうしても	死ななければならん
死ななければならん	事が
事が	分明になった
分明になった	時に
時に	起る
第二の	問題が
問題が	起る
どうせ	死ぬなら
死ぬなら	よかろう
どうして	死んだら
死んだら	よかろう
これが	問題である
第二の	問題である
自殺クラブは	有している
この	第二の
第二の	問題と共に
問題と共に	有している
起るべき	運命を
運命を	有している
死ぬ	事は
事は	苦しい
苦しい	苦しい
しかし	死ぬ
死ぬ	事が
事が	出来なければ
出来なければ	苦しい
なお	苦しい
神経衰弱の	国民には
国民には	苦痛である
生きている	事が
事が	苦痛である
死よりも	はなはだしき
はなはだしき	苦痛である
したがって	する
死を	する
苦に	する
死ぬのが	厭だから
厭だから	するのではない
苦に	するのではない
するのではない	死ぬのが
どうして	死ぬのが
死ぬのが	よかろうと
一番	よかろうと
よかろうと	心配するのである
ただ	殺してくれる
たいていの	ものは
ものは	殺してくれる
智慧が	足りないから
足りないから	放擲しておく
自然の	ままに
ままに	放擲しておく
放擲しておく	うちに
うちに	殺してくれる
世間が	殺してくれる
いじめ	殺してくれる
しかし	ものではない
一と	ある
癖	ある
ある	ものは
ものは	ものではない
世間から	殺されて
なし崩しに	殺されて
いじめ	殺されて
殺されて	満足する
満足する	ものではない
必ずや	付いて
死に方に	付いて
付いて	違ない
種々	違ない
考究の	結果
結果	違ない
嶄新な	名案を
名案を	呈出するに
呈出するに	違ない
だから	違ない
して	増加して
世界向後の	趨勢は
趨勢は	増加して
自殺者が	増加して
増加して	違ない
その	自殺者が
自殺者が	違ない
皆独創的な	方法を
方法を	もって
もって	去るに
この世を	去るに
去るに	違ない
大分物騒な	事に
事に	なりますね
たしかに	なるよ
アーサージョーンスと	云う
云う	人の
人の	かいた
かいた	脚本の
脚本の	なかに
なかに	主張する
しきりに	主張する
自殺を	主張する
主張する	哲学者が
哲学者が	あって
ところが	しないのだがね
惜しい	事に
事

君と	僕の
僕の	間には
間には	ないじゃないか
芸術も	糞も
糞も	ないじゃないか
そりゃ	思われないんです
そうですけれども	思われないんです
私は	思われないんです
どうも	思われないんです
直覚的に	思われないんです
そう	思われないんです
君が	思われなければ
直覚的に	思われなければ
そう	思われなければ
思われなければ	思うまでさ
僕は	思うまでさ
曲覚的に	思うまでさ
そう	思うまでさ
曲覚的かも知れないがと	出す
今度は	出す
独仙君が	出す
口を	出す
とにかく	許せば
人間に	許せば
個性の	自由を
自由を	許せば
許せば	許す
許す	ほど
ほど	相違ないよ
御互の	間が
間が	相違ないよ
窮屈になるに	相違ないよ
ニーチェが	担ぎ出すのも
超人なんか	担ぎ出すのも
担ぎ出すのも	変形した
全く	なくなって
この	窮屈の
窮屈の	やりどころが
やりどころが	なくなって
なくなって	変形した
仕方なしに	変形した
あんな	哲学に
哲学に	変形した
変形した	ものだね
ちょっと	見ると
見ると	見えるが
あれが	見えるが
あの	男の
男の	理想のように
理想のように	見えるが
見えるが	不平さ
ありゃ	理想じゃない
理想じゃない	不平さ
個性の	発展した
発展した	十九世紀に
十九世紀に	すくんで
すくんで	打てないから
隣りの	人には
人には	打てないから
心置	なく
なく	打てないから
滅多に	打てないから
寝返りも	打てないから
打てないから	かき散らしたのだね
大将少し	なって
やけに	なって
なって	かき散らしたのだね
あんな	乱暴を
乱暴を	かき散らしたのだね
あれを	読むと
読むと	気の毒になる
壮快と	云うより
云うより	気の毒になる
むしろ	気の毒になる
あの	声は
声は	音だ
勇猛精進の	声じゃない
声じゃない	音だ
どうしても	音だ
怨恨痛憤の	音だ
それも	あつまるのだから
そのはずさ昔は	あつまるのだから
一人	えらい
えらい	人が
人が	あれば
あれば	あつまるのだから
天下翕然として	あつまるのだから
その	旗下に
旗下に	あつまるのだから
あつまるのだから	ものさ
愉快な	ものさ
こんな	愉快が
愉快が	出てくれば
事実に	出てくれば
出てくれば	ない
何も	見たように
ニーチェ	見たように
見たように	ない
筆と	

/Users/hidareimu/.pyenv/versions/anaconda3-4.4.0/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: generator 'neco_lines' raised StopIteration
  """Entry point for launching an IPython kernel.


## 43. 名詞を含む文節が動詞を含む文節に係るものを抽出  
名詞を含む文節が，動詞を含む文節に係るとき，これらをタブ区切り形式で抽出せよ．ただし，句読点などの記号は出力しないようにせよ．

In [28]:
for i, chunks in enumerate(neco_lines(), 1):
    for j, chunk in enumerate(chunks):
        if "名詞" in [morph.pos for morph in chunk.morphs] and \
           "動詞" in [morph.pos for morph in chunks[chunk.dst].morphs] and\
            chunk.dst != -1:
            print(chunk.print_chunk(),chunks[chunk.dst].print_chunk())

どこで 生れたか
見当が つかぬ
所で 泣いて
ニャーニャー 泣いて
いた事だけは 記憶している
吾輩は 見た
ここで 始めて
ものを 見た
あとで 聞くと
我々を 捕えて
掌に 載せられて
スーと 持ち上げられた
時 フワフワした
感じが あったばかりである
上で 落ちついて
顔を 見たのが
ものの 見始であろう
ものだと 思った
感じが 残っている
今でも 残っている
第一毛をもって 装飾されべきはずの
顔が つるつるして
その後 逢ったが
猫にも 逢ったが
一度も 出会わした
真中が 突起している
中から 吹く
ぷうぷうと煙を 吹く
咽せぽくて 弱った
人間の 飲む
事は 知った
頃 知った
裏で 坐って
心持に 坐って
速力で 運転し始めた
書生が 動くのか
動くのか 動くのか
自分だけが 動くのか
動くのか 分らないが
眼が 廻る
胸が 悪くなる
音が して
眼から 出た
火が 出た
それまでは 記憶しているが
記憶しているが 分らない
あとは 分らない
事やら 分らない
気が 付いて
書生は いない
たくさん おった
兄弟が 見えぬ
一疋も 見えぬ
母親さえ 隠してしまった
姿を 隠してしまった
所とは 違って
眼を 明いていられぬくらいだ
吾輩は 棄てられたのである
上から 棄てられたのである
急に 棄てられたのである
中へ 棄てられたのである
思いで 這い出すと
笹原を 這い出すと
向うに ある
池が ある
吾輩は 見た
前に 坐って
分別も 出ない
書生がまた 来てくれるかと
迎に 来てくれるかと
試みに やって
誰も 来ない
上を 渡って
風が 渡って
日が かかる
暮れ かかる
腹が 減って来た
非常に 減って来た
声が 出ない
何でも 廻り始めた
食物の ある
所まで ある
決心を して
池を 廻り始めた
左りに 廻り始めた
そこを 我慢して
我慢して 這って行くと
無理やりに 這って行くと
事で 出た
所へ 出た
ここへ 這入ったら
竹垣の 崩れた
穴から もぐり込んだ
邸内に もぐり込んだ
もので 餓死したかも知れんのである
竹垣が 破れていなかったなら
吾輩は 餓死したかも知れんのである
路傍に 餓死したかも知れんのである
蔭とは 云った
穴は なっている
今日に 至るまで
吾輩が 訪問する
三毛を 訪問する
通路に なっている
邸へは

女で まじりましたが
私が まじりましたが
中へ まじりましたが
自分でも 弾けたと
何者かねと 問いかける
主人は 問いかける
羨ましそうに 問いかける
主人は 惚れる
顔付は しているものの
方ではない 惚れる
小説を 読んだら
中に ある
一人物が 出て来て
それが 惚れる
婦人には 惚れる
勘定を して
往来を 通る
七割弱には 恋着するという
事が 書いてあったのを
諷刺的に 書いてあったのを
書いてあったのを 見て
真理だと 感心した
男が 送っているかと
牡蠣的生涯を 送っているかと
云うのは 分らない
吾輩猫などには 分らない
人は 云うし
ためだとも 云うし
人は 云う
せいだとも 云うしまた
人は 云う
性質だからだとも 云う
どっちに したって
歴史に 関係する
人物でもないのだから 構わない
女連れを 尋ねた
気に 尋ねた
寒月君は 食い切った
面白そうに 挟んで
蒲鉾を 挟んで
箸で 挟んで
半分前歯で 食い切った
吾輩はまた せぬかと
欠けは せぬかと
二人とも 去る
方じゃありませんと しい
余所余所 しい
返事を する
ナールと 引張ったが
主人は 引張ったが
寒月君は 見る
時分だと 思った
ものか 見る
天気ですな 落ちたので
御閑なら もしましょうか
ごいっしょに もしましょうか
散歩で もしましょうか
旅順が 落ちたので
景気ですよと して
促が して
主人は 立つ
陥落より 聞きたいと
身元を 聞きたいと
顔で 考え込んでいたが
決心を した
ものと 見えて
それじゃ 出ると
紋付羽織に 着た
紀念とかいう 来着古るした
二十年 来着古るした
綿入を 着た
所々が 薄くなって
日に 透かして
裏から 当てた
つぎを 当てた
目が 見える
ときは 出る
懐手を して
ほかに 着る
面倒だから 着換えないのか
着換えないのか 分らぬ
吾輩には 分らぬ
これだけは 思われない
ためとも 思われない
両人が 出て
あとで 頂戴した
吾輩は 頂戴した
失敬して 頂戴した
寒月君の 食い切った
残りを 頂戴した
猫か あると
資格は あると
一切くらい 頂戴したって
頂戴したって 云われる
人から 云われる
人目を 忍んで
間食を するという
何も 限った
吾等猫族に 限った
御三などは 失敬している
留守中に 失敬しては
餅菓子などを

中が 聞える
笑い声さえ 聞える
陽気に 聞える
椽側から 上って
傍へ 寄って
客が 来ている
頭を 分けて
奇麗に 分けて
羽織に 着けて
袴を 着けて
主人の 手あぶりの
角を 見ると
巻煙草入れと 並んで
名刺が あるので
事も 知れた
途中からであるから 分らんが
前後が 分らんが
吾輩が 紹介した
前回に 紹介した
事に 関しているらしい
趣向が あるから
是非いっしょに 来いと
客は 云う
何ですか 食うのについて
西洋料理へ 行って
午飯を 食うのについて
食うのについて あるというのですかと
趣向が あるというのですかと
あるというのですかと 押しやる
主人は 押しやる
茶を 足して
続ぎ 足して
前へ 押しやる
趣向というのが 分らなかったんですが
時は 分らなかったんですが
私にも 分らなかったんですが
分らなかったんですが あるのだろうと
事ですから あるのだろうと
何か あるのだろうと
種が あるのだろうと
あるのだろうと 思いまして
いっしょに 行きましたか
主人は 云わぬばかりに
それ 見たかと
上に 乗った
頭を 叩く
ぽかと 叩く
茶番 見たような
癖でねと 思い出す
急に 思い出す
アンドレア・デル・サルト事件を 思い出す
君 変った
何か 変った
ものを 食おうじゃないかと
何を 食いました
献立を 見ながら
料理についての 御話しが
それから 黙っていましたよ
首を 捻って
方を なって
御覧に なって
ないようだなと おっしゃると
ボイは 黙っていましたよ
気で 云うと
チャップなどは 云うと
如何ですと 云うと
先生は おっしゃるんで
月並を 食いに
ここまで 来やしないと
意味が 分らん
ものですから 黙っていましたよ
顔を して
方を なって
御向きに なって
君 行くと
英吉利へ 行くと
万葉調が 食えるんだが
食えるんだが 圧したようで
日本じゃ 行ったって
どこへ 行ったって
版で 圧したようで
圧したようで しないと
西洋料理へ 這入る
気が しないと
大気で——全体 あるのですかな
方は あるのですかな
事が あるのですかな
あるのですかな 行かれるんですがね
何迷亭が する
洋行なんか する
もんですか あり
金も あり
時も あり
いつでも 行かれるんですがね
過去に 見立てた
洒落なんでしょうと する


水彩画を やめたから
代りに やろうと
文章でも やろうと
至りだよ 乗り気になると
僕も 乗り気になると
乗り気になると している
主人は している
疳違いを している
ところへ 失礼しましたと
寒月君が 失礼しましたと
先日は 失礼しましたと
失礼しましたと 這入って来る
名文を 拝聴して
拝聴して 退治られた
亡魂を 退治られた
ところでと ほのめかす
迷亭先生は ほのめかす
訳の わからぬ
事を ほのめかす
これも する
訳の 分らぬ
挨拶を する
左のみ 浮かれた
先日は 来たよ
紹介で 云う
越智東風と 云う
人が 来たよ
越智東風と 云う
男ですが 変っている
ところが あるのであるいは
御迷惑かと 思いましたが
こちらへ 上っても
ことについて 弁じて行き
何か 弁じて行き
どこへ 行っても
人には するのが
講釈を するのが
癖でしてね するんだいと
講釈を するんだいと
かしと 待ち構えた
迷亭君は 入れる
口を 入れる
東風と 云うのを
云うのを 読まれると
音で 読まれると
大変 するので
気に するので
迷亭先生は つまみ出す
煙草入から つまみ出す
煙草を つまみ出す
名は 越智東風ではありません
越智東風ではありません 断りますよ
越智こちですと 断りますよ
妙だねと 呑み込む
雲井を 呑み込む
底まで 呑み込む
それが 来たので
文学熱から 来たので
こ 読むと
遠近と 云う
成語に なる
姓名が 踏んでいると
韻を 踏んでいると
それだから 読むと
東風を 読むと
音で 読むと
僕が 買ってくれないと
苦心を 買ってくれないと
人が 買ってくれないと
不平を 云うのです
云うのです 変ってると
迷亭先生は 吐き返す
図に 乗って
底から 吐き返す
雲井を 吐き返す
孔まで 吐き返す
途中で して
煙が して
戸迷いを して
出口へ 引きかかる
先生は 咽び返る
煙管を 握って
ごほんごほんと 咽び返る
先日 来た
時は 笑われたと
朗読会で なって
船頭に なって
女学生に 笑われたと
主人は 云う
それと 叩く
迷亭先生が 叩く
煙管で 叩く
膝頭を 叩く
吾輩は 離れる
険呑に なったから
傍を 離れる
せんだって 御馳走した
トチメンボーを 御馳走した
何でも やるつもりだから
第二回には やるつもりだから
文士を 招待して


慵うく 感ぜら
主人に 劣らぬ
無性猫と なった
主人が 閉じ籠っているのを
書斎にのみ 閉じ籠っているのを
閉じ籠っているのを 評するのも
失恋だと 評するのも
一時は あったが
御三から 呈出された
放逐論さえ 呈出された
事も あったが
猫でないと 云う
事を 知っている
ものだから 起臥している
吾輩は 起臥している
家に 起臥している
恩を 感謝すると同時に
感謝すると同時に 表するに
活眼に対して 表するに
意を 表するに
御三が 知らずして
吾輩を 知らずして
虐待を するのは
するのは 立たない
腹も 立たない
左甚五郎が 出て来て
肖像を 刻み
柱に 刻み
スタンランが 好んで
似顔を 描くようになったら
上に 描くようになったら
描くようになったら 恥ずるであろう
鈍瞎漢は 恥ずるであろう
不明を 恥ずるであろう
三毛子は 死ぬ
黒は ならず
相手に ならず
感は あるが
人間に 出来たので
知己が 出来たので
退屈とも 思わぬ
せんだっては ある
許へ 送ってくれと
写真を 送ってくれと
手紙で 依頼した
男が ある
この間は ある
名産吉備団子を 届けてくれた
名宛で 届けてくれた
人が ある
人間から 寄せら
同情を 寄せら
事は 忘却してくる
方へ 接近して来たような
心持に なって
同族を 糾合して
糾合して 云う
雌雄を 云う
決しようなどと 云う
一人だと 思う
折さえ ある
同族を 軽蔑する
ところに 向って
勢の しからし
むるところで 評せられては
これを 評せられては
裏切りとか 評せられては
かような言語を 弄して
弄して 罵詈する
人を 罵詈する
ものに 限って
融通の 利かぬ
習癖を 脱化して
脱化して 見ると
事ばかり している
荷厄介に している
訳には 行かん
気位で 評隲したくなる
思想 評隲したくなる
言行を 評隲したくなる
見識を 有している
吾輩を 思って
毛の 生えた
ものくらいに 思って
吉備団子を 喰い尽したのは
わが物顔に 喰い尽したのは
写真も 送らぬ
不平と 云えば
見解が 自然異なるのは
吾輩は なりすましているのだから
どこまでも なりすましているのだから
人間に なりすましているのだから
なりすましているのだから 上りにくい
交際を せぬ
動作は 上りにくい
筆に 上りにくい
評判だけで

...

落第したって しないわ
叔父さんに しないわ
学資は しないわ
貰や しないわ
雪江さんは 落した
言 至って
ここに 至って
感に 堪えざるもののごとく
潸然として 落した
涙を 落した
上に 落した
茫乎として 見つめていた
涙が 起因するかを
心理作用に 起因するかを
起因するかを 研究する
顔を 見つめていた
ところへ 揃えて
御三が 揃えて
台所から 揃えて
手を 揃えて
敷居越に 揃えて
お客さまが いらっしゃいましたと
誰が 来たんだと
来たんだと 聞くと
主人が 聞くと
生徒さんでございますと 答えた
御三は 答えた
泣顔を 睨めながら
横目に 睨めながら
主人は 出て行く
客間へ 出て行く
吾輩も 廻った
ため 廻った
主人に 尾して
尾して 廻った
忍びやかに 廻った
椽へ 廻った
人間を 研究するには
研究するには 択ばないと
何か ある
波瀾が ある
時を 択ばないと
結果が 出て来ない
平凡が 持ち上がって
ために 持ち上がって
一と 云えば
口に 云えば
猫共から 見て
後学に なるような
事件が 至る
ところに あらわれてくる
横風に あらわれてくる
かくのごとく 有している
心を 有している
雪江さんも 思わなかったが
細君と している
話を している
うち 思わなかったが
はさほどとも 思わなかったが
主人が 帰ってきて
油壺を 抛り出すやいなや
死竜に して
蒸汽喞筒を して
勃然として して
深奥に して
麗質を 了った
発揚し 了った
事には あらわれて来ない
容易に あらわれて来ない
事は あらわれているが
かくのごとく あらわれて来ない
顕著に あらわれて来ない
灼然炳乎として あらわれて来ない
幸に して
主人のように 撫でたがる
毛を 撫でたがる
逆さに 撫でたがる
奇特家が おったから
狂言も 出来たのであろう
拝見が 出来たのであろう
あとさえ ついて
どこへ 行っても
男を 戴いて
旦那様に 戴いて
うちにも 出来る
経験が 出来る
年頃は 追っつ
雪江さんと 追っつ
頭を 見える
地の 隙いて
隙いて 見える
鼻を かためて
真中に かためて
方に 控えている
これと 云う
青坊主に 刈ってさえ
主人のように 延ばしたら
人目を 惹く
顔に かぎって
学問は 出来ない
事実は そうかも知れないが
着物は 分らな

腰へ ぶら下げて来て
それを 食うんだって
食うんだって 云うじゃないか
中心から 出て来るそうだ
梅干が 出て来るそうだ
一個 出て来るそうだ
梅干が 出るのを
出るのを 突進するんだと
周囲を 食い欠いて
一心不乱に 食い欠いて
突進するんだと 云うが
独仙君 気に入りそうな
君の 気に入りそうな
事が ある
友人が している
あすこへ している
奉職を している
頃 出た
印の ある
灰吹きを 買いに
名 づくべき
不思議に 思って
灰吹きなどは 出来るから
藪へ 行って切って来れば
誰にでも 出来るから
気風を あらわす
ここへ 入れなくちゃいけない
駄目を 入れなくちゃいけない
一つ 入れなくちゃいけない
—— 驚いたね
僕は 驚いたね
話を 聞いて
ところで 独習したのは
君が 独習したのは
ヴァイオリンを 独習したのは
独に して
不羣なりと あるが
楚辞に あるが
—— しろ
なに石を 上げて
勘定を しろ
勘定しなくっても 負けてるから
僕は 負けてるから
極りが つかないから
それじゃ やってくれた
君 やってくれた
才人ウェルテル君が 聞かなくっちゃ
ヴァイオリンを 習い出した
逸話を 聞かなくっちゃ
失敬すると はずして
席を はずして
方へ すり出して来た
独仙君は している
丹念に 取っては
白石を 取っては
穴を 埋め
黒石を 取っては
穴を 埋めて
内で している
計算を している
寒月君は つづける
話を つづける
ものが おっては
むやみに 厳重にしましたから
制裁を 厳重にしましたから
書生と 来たら
袴なんぞ 穿くん
第一あれから して
塩風に 吹かれつけている
男だから 済むが
あれで 済むが
女が あれじゃ
迷亭君が 這入ると
一人 這入ると
話は 飛んで行ってしまう
どっかへ 飛んで行ってしまう
貰い手が あるね
黒いのだから ありません
仕方が ありません
鏡を 見る
たんびに 出ていけない
己 出ていけない
惚が 出ていけない
女と 云う
始末に おえない
物件だからなあと 洩らした
主人は 洩らした
喟然として 洩らした
大息を 洩らした
方で しませんかと
東風君が かけた
質問を かけた
者だと 云うと
主人が 云うと
事を 云うと
迷亭先生が 注意する
小供を 連れて
さっき 出掛けた
静かだと 思った
どこ

博士に ならないばかりで
傑作も なりそうで
持ち腐れに なりそうで
同情を こめた
作を するつもりです
公けに するつもりです
それ 見たまえ
君が なるか
博士に なるか
四方八方へ 飛んだ
影響が 及んでくるよ
珠を 磨いてくれたまえ
へへへへ かけて
御心配を かけて
私には あるんです
歴然と した
女房が あるんです
秘密結婚を やったのかね
油断の ならない
苦沙弥さん 御聞き及びの
通り あるんだとさ
寒月君は あるんだとさ
妻子が あるんだとさ
結婚して たたない
一と たたない
月も たたない
うちに 生れちゃ事で
子供が 生れちゃ事で
どこで 結婚したんだと
結婚したんだと かける
主人は かける
予審判事 見たような
質問を かける
国へ 帰ったら
うちで 待ってたのです
所へ 持って来た
鰹節は 貰ったんです
結婚祝に 貰ったんです
親類から 貰ったんです
三本 祝うのは
うちを 持って来たのです
三本だけ 持って来たのです
ほかへ やりゃ
中で するような
鉢合せを するような
鉢合せを しないでも
ところを 鉢合せるんだから
事なら 構いっこないよ
鉢が 合ったって
鴛鴦歌を 作った
こちらへ 向け
結婚式にはまた 作りますから
詩人だけ あって
方へ 断わったかいと
主人は している
金田を している
気に している
訳が ありません
方で くれとも
先方へ 申し込んだ
事は ありませんから
なあに 黙ってても
今時分は 知れていますよ
探偵が かかって
二十人も かかって
一部 残らず
探偵と 云う
言語を 聞いた
主人は して
顔を して
そんなら 黙っていろと
探偵について 述べられた
事を 述べられた
大議論のように 述べられた
際に 抜くのが
懐中を 抜くのが
スリで 釣るのが
際に 釣るのが
胸中を 釣るのが
間に はずして
雨戸を はずして
泥棒で 読むのが
間に 滑らして
口を 滑らして
心を 読むのが
ダンビラを 刺して
上へ 刺して
無理に 着服するのが
金銭を 着服するのが
おどし文句を 並べて
いやに 並べて
探偵と 云う
一族で 置ける
風上に 置ける
奴の 云う
事を 聞くと
癖に なる
大丈夫です 襲撃したって
探偵の 襲撃したって
二千人 襲撃したって
風上に 整えて
隊伍を 整えて
襲撃したって 怖

みんな 貰う
訳にゃ いかないでしょうか
みんなですか 張りたい
それは 張りたい
慾 張りたい
主人は 言い放ったので
叱りつけるように 言い放ったので
それじゃ 貰わんですねと
どれも 貰わんですねと
念を 押しながら
写真を 収めた
一枚に 収めた
ポッケットへ 収めた
前祝に 買うて来ました
酒屋で 買うて来ました
一つ 飲んで下さい
主人は 抜かせる
手を 呼んで
拍って 呼んで
下女を 呼んで
栓を 抜かせる
五君は 祝した
コップを 捧げて
艶福を 祝した
ここに いる
諸君を 招待しますが
披露会に 招待しますが
招待しますが 出てくれるでしょうねと
みんな 出てくれますか
いやだと 答える
主人は 答える
不人情じゃないが 出ないよ
おれは 出ないよ
袴くらい しますたい
人中へも 出るがよ
人に 紹介して上げます
癒らんでも 差支えない
そげん頑固張りなさるなら やむを得ません
あなたは 来てくれますか
僕かね 是非行くよ
栄を 得たい
そこ いらだろうと
仲人が 出来ても
二人 出来ても
人間として 出席するよ
寒月君は 出てくれるでしょうね
関係も あるから
事に します
僕の 作った
曲を 奏するのを
楽隊が 奏するのを
奏するのを きき落すのは
前で 朗読したいです
新体詩を 朗読したいです
私は 生れてから
一杯ビールを 飲みますと
自分で 買って来た
ビールを 飲んで
一人で 飲んで
真赤に なった
日は 暮れて
死骸が 乱す
算を 乱す
なかを 見れば
火は 消えている
昔に 消えている
連中も 尽きたと
興が 尽きたと
独仙君が 立ち上がる
僕も 帰ると
口々に 出る
玄関に 出る
寄席が はねた
あとのように 淋しくなった
座敷は 淋しくなった
主人は 入る
夕飯を すまして
書斎に 入る
妻君は 縫う
襟を かき合せて
不断着を 縫う
小供は 寝る
枕を 並べて
下女は 行った
湯に 行った
呑気と 見える
人々も 見ると
底を 叩いて
音が する
悟ったようでも 踏まぬ
足は 踏まぬ
ほかは 踏まぬ
絵に かいた
寒月君は 連れて来た
珠磨りを やめて
お国から 連れて来た
奥さんを 連れて来た
順当が 続くと
東風君も したら
十年 したら
新体詩を 捧げる
非を 悟るだろう
三平君に 至っては
水に 住む
山に 住む
三

/Users/hidareimu/.pyenv/versions/anaconda3-4.4.0/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: generator 'neco_lines' raised StopIteration
  """Entry point for launching an IPython kernel.


## 44. 係り受け木の可視化  (▲)
与えられた文の係り受け木を有向グラフとして可視化せよ．可視化には，係り受け木をDOT言語に変換し，Graphvizを用いるとよい．また，Pythonから有向グラフを直接的に可視化するには，pydotを使うとよい．



In [49]:
import pydot_ng as pydot
edges = []
for i, chunks in enumerate(neco_lines(), 1):
    if i == 7:
        for j, chunk in enumerate(chunks):
            if chunk.dst != -1:
                src_chunk = chunk.print_chunk()
                dst_chunk = chunks[chunk.dst].print_chunk()
                edges.append([[j,src_chunk],[chunk.dst,dst_chunk]])
        break
print(edges)
g = pydot.Dot(graph_type = "digraph")
def recievied_relation_vis(edges):
    for edge in edges:
        id1 = str(edge[0][0])
        label1 = str(edge[0][1])
        id2 = str(edge[1][0])
        label2 = str(edge[1][1])

        # ノード追加
        g.add_node(pydot.Node(id1, label=label1))
        g.add_node(pydot.Node(id2, label=label2))

        # エッジ追加
        g.add_edge(pydot.Edge(id1, id2))

    g.write_png('result.png')

recievied_relation_vis(edges)

[[[0, '何でも'], [1, '薄暗い']], [[1, '薄暗い'], [3, '所で']], [[2, 'じめじめした'], [3, '所で']], [[3, '所で'], [5, '泣いて']], [[4, 'ニャーニャー'], [5, '泣いて']], [[5, '泣いて'], [7, '記憶している']], [[6, 'いた事だけは'], [7, '記憶している']]]


## 45. 動詞の格パターンの抽出  
今回用いている文章をコーパスと見なし，日本語の述語が取りうる格を調査したい． 動詞を述語，動詞に係っている文節の助詞を格と考え，述語と格をタブ区切り形式で出力せよ． ただし，出力は以下の仕様を満たすようにせよ．

動詞を含む文節において，最左の動詞の基本形を述語とする  
述語に係る助詞を格とする  
述語に係る助詞（文節）が複数あるときは，すべての助詞をスペース区切りで辞書順に並べる
「吾輩はここで始めて人間というものを見た」という例文（neko.txt.cabochaの8文目）を考える． この文は「始める」と「見る」の２つの動詞を含み，「始める」に係る文節は「ここで」，「見る」に係る文節は「吾輩は」と「ものを」と解析された場合は，次のような出力になるはずである．  

始める  で  
見る    は を  
このプログラムの出力をファイルに保存し，以下の事項をUNIXコマンドを用いて確認せよ．  

コーパス中で頻出する述語と格パターンの組み合わせ  
「する」「見る」「与える」という動詞の格パターン（コーパス中で出現頻度の高い順に並べよ）



In [88]:
f = open("result_kaku_frame.txt","w+")
for i, chunks in enumerate(neco_lines(), 1):
        for j, chunk in enumerate(chunks):
            tmp = ""
            if chunk.srcs != []:
                for morph in chunk.morphs:
                    if morph.pos == "動詞":
                        tmp = morph.base +"\t"
                if tmp:
                    for src in chunk.srcs:
                        for morph in chunks[src].morphs:
                            if morph.pos == "助詞":
                                tmp += morph.surface + " "        
            if tmp:
                f.write(tmp+"\n")
                print(tmp)
f.close()

生れる	で 
つく	か が 
泣く	で 
いる	て だけ は 
始める	で 
見る	は を 
聞く	で 
捕える	を 
煮る	て 
食う	て 
思う	から 
られる	に 
られる	て と 
する	
ある	が 
落ちつく	で 
見る	て を 
見る	の 
思う	と 
いる	が でも 
れる	をもって 
する	が 
逢う	に も 
する	も 
いる	が 
吹く	から を 
する	
弱る	て 
飲む	の 
知る	は 
坐る	で に 
おる	て 
する	
始める	が と で 
動く	が 
動く	か だけ が 
分る	か 
廻る	が が 
なる	が 
助かる	
いる	と 
する	と が 
出る	て と て から が 
いる	まで は 
考え出す	
分る	て が は やら として も 
付く	が 
見る	て 
いる	と は 
おる	
見える	が も 
しまう	さえ を 
違う	と は 
られる	を 
這い出す	
見る	て 
られる	は から に へ 
這い出す	で を 
ある	と に が 
坐る	に 
する	て 
考える	と 
見る	は て 
出る	も 
する	
泣く	て 
くれる	が に 
考え付く	て か と 
やる	に 
見る	て 
来る	が も 
渡る	を と が 
かかる	て が 
来る	が に 
出る	て も が 
ある	の 
ある	まで 
する	と を 
そる	て 
始める	で も を に 
する	を 
行く	て に 
出る	て と で へ 
這入る	へ 
なる	
思う	と 
崩れる	の 
もぐり込む	て から に 
いる	が 
知れる	て は に 
云う	と は 
至る	に 
する	まで が を 
いる	は に 
忍び込む	へ は 
分る	ものの か 
なる	に 
減る	は 
来る	が 
なる	で が 
行く	へ へ と 
考える	から 
這入る	に 
おる	と は て 
見る	を 
する	で は に 
逢う	に 
見る	より で を 
つかむ	を 
抛り出す	は や で へ 
思う	と 
ねぶる	を 
いる	から て を に 
出来る	に は が 
見る	を 
上る	は て へ 
れる	
上る	は て は 
れる	て は 
繰り返す	でも を 
いる	を 
云う	に と 
なる	は 
やる	んで を 
下りる	て て から が 
する	が に 
いう	と 
来

見る	は て を 
受ける	でも を 
する	て を 
なる	も くらい 
する	で も 
いる	を 
する	
来る	が 
なる	と て が に 
いう	と 
する	で は を 
いる	て でも より 
話す	が に て という 
来る	か へ に 
いる	と を って 
有る	が 
並べる	ばかり 
帰る	て は 
求める	を 
話す	
する	を 
来る	に 
する	から 
行く	て て が 
聞く	が を 
打つ	て を 
する	を 
いる	から に 
思う	と 
向く	から て も へ が 
ひねくる	を 
見る	ので と ながら 
いう	を 
向く	へ が 
する	を 
引張る	と は て を 
いる	は かい から べ ん が へ くらい ずつ 
違う	
笑う	で と が 
いる	と は が 
する	を 
転じる	か ね と は を 
食う	で を 
食う	て ね を 
食う	を 
する	を で 
欠ける	と と が 
かける	で が 
知れる	に は 
なる	かも が に は 
叩く	な と で を 
ある	か 
負ける	に だって 
ある	も 
なる	
なぐる	さ と に を 
やる	も と を 
戻す	て ね と は を へ 
ならぶ	で でも に 
なる	も くらい に 
れる	と でも 
まじる	は で が へ 
弾ける	で も 
思う	が と 
問いかける	か ね と は に 
いる	は 
読む	を 
ある	に 
来る	が 
惚れる	は て ものの は て て が に は 
する	を 
見る	て 
通る	と を 
する	に は 
ある	が に 
見る	て を 
する	と 
いる	が を 
云う	て か と 
分る	は など に は 
云う	は と も 
云う	と も 
云う	し は し は て から と も 
する	に 
する	って に 
構う	で も から 
尋ねる	を に 
挟む	に を で 
食い切る	は で で 
する	は は 
する	か と 
去る	と も 
しいる	じゃ と 
する	を 
引張る	と は 
略す	ほど を 
いる	が て 
思う	と 
もす	に で 
落ちる	な か が 
する	よ と が 
見る	は か て 
聞く	より を 
云う	と 
いる	で 
する	で が を 
見える	と 
出る	じゃ 
する	と 
思い

する	と 
いる	て を 
来る	て と が の に 
思う	と 
込める	を 
おく	て て 
しまう	て て か 
飛び込む	
ぱちつかせる	と が を 
問う	て 
行く	まで 
思う	と は 
つまむ	と が を と 
なる	は が 
さめる	が 
見る	て 
ある	と 
濡れる	も 
飲む	を 
する	は が も 
飛び込む	
気が付く	と 
見渡す	て を 
驚く	と 
飛び込む	へ 
いる	で 
間違う	
飛び下りる	て へ 
出る	だけ で の 
行く	へ 
出来る	が 
笑う	
いる	は ながら の を 
いる	と 
なる	に 
云う	と 
する	で に 
驚かす	を 
なる	は 
する	か ね と が 
行く	に 
いる	で を 
見える	と 
開く	を 
ある	に も 
負ける	と 
出す	が て を 
ある	って が 
笑う	な と が 
いる	に が 
まぜ返す	じゃ か と が 
違う	は 
くれる	が に を 
云う	て と 
やる	て て 
聞く	は と 
する	が を 
云う	から が て と 
よす	は 
する	から と は に 
なる	に 
来る	を 
云う	と が と 
よす	から 
云う	と 
する	を 
引き下がる	は と は て 
なる	に 
云う	と が 
聞く	は が 
知る	は も か 
せる	に 
行く	に 
下す	て 
いる	から って も 
する	が と を 
行く	が 
行く	
しいる	て も 
云う	と 
行く	から に 
れる	たって 
云う	
行く	へ 
云う	と 
在る	が 
する	て と 
する	て を 
踏む	を 
脱す	で を 
する	を 
やめる	は 
云う	から が と 
する	は を 
知る	と から なんか 
踏む	を 
来る	も で に 
かかる	の 
する	から って を 
すむ	が で も 
泣く	と 
出す	が て から は を 
行く	でも 
する	に 
くる	を 
行く	て で 
する	と を 
する	まで に へ 
いける	に ちゃ 
する	
れる	て 
行く	まで に 
聞き返す	と 
行く	
とる	て を 
れる	ちゃ 
られる	から と から 
述べる	と を 
過ぎる	じゃ を 
押す	を 
見る	ね と て 
答える	とも と 
出す	に は から に が 
聞

ある	が は として 
絞める	で も 
云う	と 
ある	と が が 
知る	が か 
死ねる	と で 
ある	が が に 
云う	と 
絞める	を 
ある	が 
飛び降りる	から 
しまう	で に は に が 
過ぎる	が 
着く	と は て が へ 
死ねる	ので 
手伝う	に が 
さす	て 
話す	と 
くる	へ 
出る	と は と に が 
死ぬ	
浮かれ出す	な と まで 
ある	が 
延びる	を と が ばかり 
計る	が 
見る	は て 
ある	から は 
釣る	
貰う	など は て 
延びる	
なる	
知れる	は ね ちゃあ に かも 
向く	ぜ と が を 
延びる	くらい が 
生き返る	て 
ある	が 
聞く	と は か と 
いる	は に って 
延びる	て が 
云う	
延びる	と が 
云う	と 
壊れる	から より 
止める	から ね じゃ 
する	と は 
ある	
する	に まで 
いる	は て は で 
挟む	を 
する	と が を 
やめる	で 
しまう	が ので て 
振る	を 
起る	か で 
過ぎる	は 
来る	が は の として の 
着く	に 
聞く	を 
知らせる	を 
来る	に 
示す	と かい と を 
合う	は 
及ぶ	を に 
思う	と 
来る	は て を 
云う	を 
云う	と 
おく	
貰う	て て 
する	だけ は と に 
いる	と は 
行く	に が に 
よす	に 
参る	ば に など へ 
知る	を 
留める	が を 
云う	に と 
ある	が が 
てる	
知る	か にゃ 
行く	へ 
ある	は 
いる	
する	で を 
思う	と 
知る	が を 
務まる	て も は 
なる	から な と は に 
這入る	へ が 
いる	て 
来る	が て と へ が で 
する	が は で に か 
見る	が て 
たまる	て 
やる	
見る	て 
出来る	
考える	で 
する	ね 
れる	と は 
見る	が を 
買う	て を 
くれる	が 
聞く	て か と 
云う	じゃ か は ばかり から と 
得る	を 
聞く	が は に 
分る	
問い掛ける	で 
得る	が から を 
分る	
思う	か と 
れる	と を 
する	と 
較べる	に 
表する	と は て を 
くる	へ が に 
取り巻く	

振り立てる	じゃ か と を 
懲らしめる	
やる	に 
いる	にゃ も 
いる	から な が 
いる	が 
やる	から で から 
分る	て は は 
揃う	ばかり 
驚く	が と 
聞く	は かい と 
教える	か に 
云う	で は だって 
する	
遇う	に 
おりる	にゃ が 
云う	から は で と 
れる	と 
答える	て は と に 
いる	んで と 
ある	て が 
困る	の に て 
云う	から と 
云う	を 
生やす	に って よ に なんか 
生やす	を 
云う	とか 
返る	
思う	と 
分る	が か 
言う	ものの 
受ける	を 
ある	って を 
出る	に は は も 
来る	の 
ある	か は も 
いる	
隔てる	で と を 
する	て で が 
ある	に も か が 
向ける	に と へ を 
来る	
見る	て 
いる	と が で か で 
いる	が と 
もつ	を 
推す	て 
する	が を 
せしめる	て を 
拝する	で を 
出来る	が 
いる	に を 
受合う	で か か 
する	から など を 
考える	て 
見る	て 
惹く	を 
れる	と と も 
いる	は って 
聞える	が も 
きく	に 
おく	を 
おくれる	て て 
いいかえる	ね から ね 
分る	かい 
取る	を 
取れる	だって 
取れる	
とる	
おひゃらかす	よ に を 
分る	なんぞ が 
云う	に へ って 
する	
弁じる	で でも 
てる	を か 
おる	へ へ へ へ へ 
あずかる	に 
聞く	なんか 
てる	や ね 
する	を 
しまう	に と を 
てる	か よ 
分る	ちゃ 
なさる	じゃ か 
切る	から 
起す	を 
廻す	は て を と 
いる	で が 
出す	て に 
出来る	は に 
飛び下りる	に 
もぐり込む	と て へ 
する	を が 
開ける	て を 
する	が 
来る	か 
いる	な と に 
いらっしゃる	が 
する	て と で と が 
食わせる	よ と は を 
ある	が 
来る	から を 
おっしゃる	で と 
知る	ね 
食わせる	て ば と は を 
ある	で が 
利かす	を 
する	と は て を 
知る	で も 
する	が を 
する	わ を 
する	て は が に 
結う	に 
つく	

...

行く	は て て 
残る	は へ 
坐る	と に 
する	を 
いる	なり て 
云う	
持つ	を 
連れる	へ 
行く	て 
いたる	
する	を 
いる	と は で に 
する	
驚く	で 
く	の 
ある	は が 
する	を 
する	なぞ は に 
なる	に くらい に 
見る	と 
なる	に 
知れる	も に かも 
持つ	の 
利く	が 
する	は を に 
よる	に 
云う	と 
行く	は へ と 
行く	まで 
する	だけ たって は 
られる	は 
行く	へ 
ある	と は に が 
する	を 
承る	から 
述べる	から と を の に 
立てる	
来る	に 
てる	を 
云う	と 
聞く	を 
いる	て は 
する	を 
及ぶ	て を に 
帰る	で 
云う	と 
直す	が も 
いる	が 
思う	と 
持ち出す	が を に 
いる	を 
なる	から は に 
聞く	を 
ある	が 
推す	を 
見る	から て 
聞く	の 
とく	って の 
いる	に 
する	と と も 
変る	
知れる	じゃ から が 
ある	が 
立ち行く	から も で 
云う	と 
する	から 
てる	て 
いる	も から で 
振る	など も 
来る	へ に 
云う	と 
する	て を 
立つ	まで 
繰り返す	を 
やめる	て も て 
寝る	が 
云う	から じゃ か と 
切る	と 
やる	て を 
する	と さ は に は 
くれる	
する	
寝かす	に て 
出る	が 
悟る	
云う	を 
見える	けれども と 
する	て に 
まわる	が に 
くれる	
責める	て と 
する	に は 
行く	へ 
貼る	へ を 
やる	から て て 
する	で が 
れる	に 
用いる	に 
ある	は ので と が 
おく	さえ 
云う	から と 
ごまかす	から 
いる	は に を 
云う	
思う	と 
する	て 
しまう	から て 
起きる	
見る	て 
ぶらさがる	から が 
いる	と て に 
なる	より 
逢う	
来る	ばかり に 
する	を 
行く	て て 
す	で を 
思う	と 
しまう	に 
する	も に 
やる	て から て を 
てる	と 
云う	の 
受ける	を 
見る	と を 
言う	の 
いける	は を に 
なる	と 
てる	を 
飛び降りる	

する	を と 
いる	て て と 
云う	は と 
云う	と 
ある	から は 
見る	を 
なる	に 
殖える	が でも 
衰える	ば は 
いる	の 
いる	の 
いる	に 
心得る	て は 
思う	と 
見える	と 
比べる	に 
云う	と 
なる	と て は 
食う	
もつ	を 
済ます	て に を 
着る	を 
乗る	て へ 
及ぶ	は て へ に 
あける	を 
てる	に を 
聞く	か と 
笑う	は へ へ へ と 
ある	の 
押す	ぜ と を 
出掛ける	が で から 
済ませる	を 
する	よ と 
する	よ と を 
なさる	か 
叱る	と 
言う	に 
せる	て 
おっしゃる	だって 
動じる	と て よ と は 
至る	に 
思う	も て に 
出す	から を 
繰り返す	て 
見る	か て 
いる	と で と 
知る	と も 
出す	は に へ を 
知る	も 
込む	に へ 
至る	に 
知る	て は 
する	か て を 
いる	に と 
出す	を 
取りかかる	は じゃ で と て に 
なる	に 
起る	は も 
来る	が が に 
まがる	の 
履く	を 
引きずる	て を 
ふくらます	を の に 
乞う	て から も 
来る	て に 
やって来る	に 
する	と を 
行く	て て 
云う	とか 
出る	へ 
あるく	て 
逢える	ば 
来る	は と へ 
おろす	て て へ を 
上がる	に 
思う	と 
出る	から を 
来る	から て て 
ある	か が 
する	を 
上がる	から 
いらっしゃる	て から 
来る	が 
はねる	
行く	へ 
行く	へ 
這入る	
れる	に 
戻る	が 
出る	が 
来る	から に 
来る	が 
出掛ける	が 
いらっしゃる	は 
起こす	は から 
怒る	ほど と 
おこす	なんか も まで に 
云う	と 
起こす	から 
潜る	へ 
する	て も 
おこす	から に 
云う	は と から か 
しまう	
怒る	に 
勤まる	で が 
怒る	
云う	が と 
云う	と 
言う	でも の 
する	に 
せる	か 
思う	と 
云う	を 
なる	と に 
もらう	を 
いる	に も 
いる	
云う	って と 
ある	が 
買う	
する	か って て 
する	も 
なさる	
来る	が 


散らす	で 
なる	て も 
結ぶ	て 
する	を 
いる	て を 
なる	も は で は に も 
云う	と 
覗く	に 
見る	て 
こぼれ落ちる	が から 
合う	まで に 
いる	て 
云う	から と 
どく	に 
貰う	て 
行く	に も 
申す	と 
命ずる	て に を 
あきらめる	て と 
する	て て も 
いる	
する	
出来る	に も 
する	を 
あらわれる	が に 
する	と 
いる	は を 
云う	て と 
差支える	で ば て も 
する	が で 
出来る	が 
する	と 
縮める	を から と 
立つ	の 
ある	
踏み出せる	て も 
する	で に を 
得る	ば と は て と 
求める	を 
評す	と に 
ある	
云う	
限る	に 
引きずり出す	か て から を 
始める	と は て を 
とる	を 
いる	は て を が に 
ある	に は が 
行く	て は に 
ある	でも が 
くる	へ 
知れる	に は は 
死ぬ	
する	を も 
行く	と 
なる	に 
来る	より 
生ずる	て を 
おく	
遣る	
思う	と 
やる	を と 
する	
する	も 
しまう	て 
れる	を 
しまう	ちゃ 
待つ	
云う	から 
てる	
仕る	て 
くれる	を 
待つ	も 
隣る	に 
くれる	も て 
言う	を 
生きる	か 
云う	か と 
くる	って から け 
知る	は は 
どける	
まう	て も から 
する	から を 
待つ	に 
仕る	を 
どける	
まう	
云う	と 
する	なんか 
捌ける	
殺す	で も 
なる	ば は に 
負ける	から 
構う	て も 
構う	は て も 
す	が に は 
てる	に を 
なる	か に 
思う	と 
ある	が 
あきらめる	じゃ 
あきらめる	
下す	と は へ と を 
いる	で が に を 
する	に が を 
いる	て と に は んで て 
ある	に に 
取り出す	で 
感じる	に 
いる	は は くらい ながら 
する	を 
いる	は て を に 
開く	で と は を 
来る	ばかり に から 
ある	が 
いる	て け 
れる	から 
くる	
及ぶ	で に は 
云う	さ と は の を 
する	を 
有る	だって に も は 
取り上げる	を 
行く	へ

ある	と が 
云う	から と 
する	を 
云う	と 
ある	に が 
云う	と 
いる	は を 
云う	て と 
進む	が 
したがう	に 
行く	は て と 
なる	に て から は も と は 
云う	と 
評す	が を 
かかる	の 
入る	に 
通る	を 
写す	に を 
見る	て 
済む	が 
出来る	ほど も を の 
評す	て ば と 
いる	て は は を 
おれる	て も 
至る	が 
つける	に 
いる	て も 
つく	が に 
なる	ばかり で 
なる	に ばかり が 
する	ばかり を 
なる	て から で から まで 
云う	とか 
ある	が 
しまう	は て に 
掠める	を 
する	て を 
云う	と 
出来る	は から て は 
捕まる	も 
見つかる	か 
云う	か と 
離れる	が を 
得る	から が 
する	
なる	に 
なる	か に 
寝る	か と 
醒める	て も 
つづける	は て も 
得る	から が 
する	
入る	て に 
得る	まで も 
出す	と が 
なる	に 
いる	
いる	は を 
忘れる	を 
教える	と 
忘れる	を 
教える	は な と 
違う	から 
云う	と 
いる	をもって 
云う	に が と 
忘れる	て を 
する	を 
いる	は て も を 
する	など と 
いる	も が 
行く	が へ に 
する	て を 
心づく	が と も 
出す	を 
とる	に に て を で へ 
なる	から に 
入る	て 
する	を 
とる	て は て で を へ 
聞く	は を 
つける	と が を 
ある	の 
する	で が 
する	て を 
ある	が 
済む	が 
洗う	で を 
入れる	を へ 
出す	て 
なれる	は に 
見える	と 
あてる	を へ 
しまう	て て を 
祝す	が を 
云う	と 
飲み干す	ながら を に 
並みいる	で 
劣る	も 
挙げる	と を 
祝す	て を 
云う	と 
ある	も 
てる	よ と 
云う	が 
始める	が 
する	て に 
云う	と 
おろす	から ながら と へ を 
いる	に 
出す	が 
出す	
出る	は 
する	と 
向く	が を 
する	て か を 
かける	が へ を 
失う	は を 
云う	さ て と 
入る	の 
ある	も 


/Users/hidareimu/.pyenv/versions/anaconda3-4.4.0/lib/python3.6/site-packages/ipykernel_launcher.py:2: DeprecationWarning: generator 'neco_lines' raised StopIteration
  


## 46. 動詞の格フレーム情報の抽出  
45のプログラムを改変し，述語と格パターンに続けて項（述語に係っている文節そのもの）をタブ区切り形式で出力せよ．45の仕様に加えて，以下の仕様を満たすようにせよ．

項は述語に係っている文節の単語列とする（末尾の助詞を取り除く必要はない）  
述語に係る文節が複数あるときは，助詞と同一の基準・順序でスペース区切りで並べる  
「吾輩はここで始めて人間というものを見た」という例文（neko.txt.cabochaの8文目）を考える． この文は「始める」と「見る」の２つの動詞を含み，「始める」に係る文節は「ここで」，「見る」に係る文節は「吾輩は」と「ものを」と解析された場合は，次のような出力になるはずである．  

始める  で      ここで  
見る    は を   吾輩は ものを  



In [87]:
for i, chunks in enumerate(neco_lines(), 1):
        for j, chunk in enumerate(chunks):
            tmp = ""
            if chunk.srcs != []:
                for morph in chunk.morphs:
                    if morph.pos == "動詞":
                        tmp = morph.base
                if tmp:
                    particle_candi = []
                    chunk_candi = []
                    for src in chunk.srcs:
                        for morph in chunks[src].morphs:
                            if morph.pos == "助詞":
                                particle_candi.append(morph.surface)
                                chunk_candi.append(chunks[src].print_chunk())
                    print(tmp +"\t"+ " ".join(particle_candi)+"\t"+" ".join(chunk_candi))            


生れる	で	どこで
つく	か が	生れたか 見当が
泣く	で	所で
いる	て だけ は	泣いて いた事だけは いた事だけは
始める	で	ここで
見る	は を	吾輩は ものを
聞く	で	あとで
捕える	を	我々を
煮る	て	捕えて
食う	て	煮て
思う	から	なかったから
られる	に	掌に
られる	て と	載せられて スーと
する		
ある	が	感じが
落ちつく	で	上で
見る	て を	落ちついて 顔を
見る	の	ものの
思う	と	ものだと
いる	が でも	感じが 今でも
れる	をもって	第一毛をもって
する	が	顔が
逢う	に も	猫にも 猫にも
する	も	一度も
いる	が	真中が
吹く	から を	中から ぷうぷうと煙を
する		
弱る	て	咽せぽくて
飲む	の	人間の
知る	は	事は
坐る	で に	裏で 心持に
おる	て	坐って
する		
始める	が と で	おったが すると 速力で
動く	が	書生が
動く	か だけ が	動くのか 自分だけが 自分だけが
分る	か	動くのか
廻る	が が	分らないが 眼が
なる	が	胸が
助かる		
いる	と	助からないと
する	と が	どさりと 音が
出る	て と て から が	思っていると 思っていると して 眼から 火が
いる	まで は	それまでは それまでは
考え出す		
分る	て が は やら として も	記憶しているが 記憶しているが あとは 事やら 考え出そうとしても 考え出そうとしても
付く	が	気が
見る	て	付いて
いる	と は	見ると 書生は
おる		
見える	が も	兄弟が 一疋も
しまう	さえ を	母親さえ 姿を
違う	と は	所とは 所とは
られる	を	眼を
這い出す		
見る	て	這い出して
られる	は から に へ	吾輩は 上から 急に 中へ
這い出す	で を	思いで 笹原を
ある	と に が	這い出すと 向うに 池が
坐る	に	前に
する	て	坐って
考える	と	よかろうと
見る	は て	吾輩は 考えて
出る	も	分別も
する		
泣く	て	して
くれる	が に	書生がまた 迎に
考え付く	て か と	来てくれるかと 来てくれるかと 来てくれるかと
やる	に	試みに
見る	て	やって
来る	が も	見たが 誰も
渡る	を と が	上を さらさらと 風が
かかる	て が	渡って 日が
来る	が に	

とる	でも ね が は	たんとでもねえが たんとでもねえが たんとでもねえが 三四十は
つづける	を	語を
引き受ける	は で でも	二百は 一人で いつでも
合う	は て が って は に	彼は つづけて 引き受けるが いたちってえ 奴は 手に
向う	に	いたちに
逢う	て に	向って 目に
打つ	と を	へえなるほどと 相槌を
ぱちつかせる	を	眼を
云う	は て	黒は ぱちつかせて
持つ	が を	亭主が 袋を
込む	て へ	持って 下へ
いる		
喰う	が	野郎が
飛び出す	て	喰って
思う	と	飛び出したと
する	と	ふんと
見せる	て	感心して
える		
追っかける	って で	こん畜生って 気で
追い込む	て へ	追っかけて 中へ
思う	と	追い込んだと
やる	ねえ	思いねえ
やる	ね と	やったねと やったねと
なる	て に	御めえいざってえ段に 御めえいざってえ段に
がる	と を	なると 奴め最後っ屁を
見る	を	いたちを
至る	に	ここに
感ずる	て を	至って 臭気を
揚げる	を	前足を
する	は て を	彼は 揚げて 頭を
する	も が	吾輩も 感じが
やる	を	景気を
思う	て と	付けてやろうと 付けてやろうと
れる	に	君に
捕る	を	鼠を
食う	が で ばかり	捕るのが 名人で 鼠ばかり
肥る		
とる	を	御機嫌を
する	は は に も を	君は 質問は 不思議にも 不思議にも 結果を
する	として	喟然として
いう	は て	彼は 大息して
える		
つまる	と	えると
稼ぐ		
とる	で を	稼いで 鼠を
える	ほど	人間ほど
いる	って は に	とったって—— 奴は 世の中に
とる	の	人の
がる	を	鼠を
行く	て へ	取り上げやがって 交番へ
あがる	て	持って行きゃ
捕る	じゃ が	交番じゃ 誰が
分る	か	捕ったか
くれる	から に ずつ	分らねえから たんびに 五銭ずつ
儲ける	なんか で くらい	亭主なんか 御蔭で 壱円五十銭くらい
いやがる	て	儲けて
食わせる	に を	癖に 碌なものを
する	も	事も
わかる	ぜ も は	泥棒だぜさすが 黒も 理窟は
見える	と	わかると
怒る	て	見えて
いる	で を	容子で 毛を
なる		
する	に を	加減に 場を
帰る	は から て へ	吾輩は 気味が悪くなったから 胡魔化し

なる	と に	はずすと 知らずに
する	は に ながら を	吾輩は 刹那に 猫ながら 真理を
する	を	動物を
しむ	は て を も て	機会は して 事をも 事をも 敢て
云う	を	実を
食う	は と を	吾輩は 云うと 雑煮を
する	を	様子を
する	ば	熟視すれば
なる	ほど	ほど
食う	て	気味が悪くなって
なる	が	食うのが
開ける	でも を	御三でも 勝手口を
近付く	が へ	足音が こちらへ
得る	を	近付くのを
見棄てる	を	椀を
浮ぶ	は は まで に	吾輩は 事は 来年まで 念頭に
来る	も	誰も
来る	て て も も	いくら躇していても いくら躇していても いくら躇していても 誰も
食う		
食う	か	食わぬか
れる	か と	食わぬかと 食わぬかと
する	が	心持が
込む	を	中を
くれる	ながら か	覗き込みながら 誰か
念じる	は て ば と	吾輩は 来てくれればいいと 来てくれればいいと 来てくれればいいと
くれる	も	誰も
なる	は を	吾輩は 雑煮を
する	を へ	重量を 底へ
食い込む	に て を ばかり	落すようにして 落すようにして 角を 一寸ばかり
込める	を	力を
付く	くらい て	くらい 込めて
切れる	から	食い付いたのだから
思う	と	よかろうと
する	て を	思って 歯を
引ける	が と と	噛み切れる訳だが 引こうとすると 引こうとすると
する		
とれる	と と が	噛み直そうとすると 噛み直そうとすると 動きが
づく	な と	魔物だなと 魔物だなと
落ちる	へ で も	沼へでも 沼へでも 沼へでも
抜く	が を	人が 足を
沈む	と に	抜こうと たびに
噛む	ば	噛めば
なる	に ほど が	沈むように ほど 口が
なる	が	歯が
ある	は	歯答えは
ある	が	歯答えが
つける	だけ で を	あるだけで あるだけで 始末を
出来る	が が	あるが 事が
評す	が を	美学者迷亭先生が 主人を
ある	て は が	評して 君は 事が
いう	を	事を
割り切れる	も に	餅も 同じように
噛む	で も	噛んでも 噛んでも
割る	で を	三で 十を
つく	の	尽未来際方の
れる	と	あるまいと
する	は に	吾輩は 真理に
する	は に を	動物は 直覚的に 適不適を
する	は まで	真理は 二つまで
いる	が	餅が


見る	から	来たから
いる	だけ に	年寄だけに 年寄だけに
思う	と まで も を の に	見ると いつまでも いつまでも 僕を 小供のように 小供のように
する	を	夜間外出を
焚く	を	ストーブを
やる	て を か に	焚いて 室を 煖かに 煖かに
引く	て と を	してやらないと してやらないと 風邪を
ある	が とか が	いいが 引くとか 注意が
いく	で は は	他人では 他人では こうは
する	と も だけ は に	いかないと 僕も 時だけは 時だけは 大に
つける	に	それに
いる		
する	か	何か
揚げる	で も て を	大著述でもして 大著述でもして 大著述でもして 家名を
なる	て は	揚げなくては 揚げなくては
いる	の	母の
する	に を	うちに 天下を
しめる	て に を	して 文壇に 迷亭先生あるを
云う	と	知らしめたいと
なる	に	気に
行く		
始まる	が	戦争が
する	を	辛苦を
いる	て は て に	始まって 人達は して ために
いる	て のに で も の に に	いているのに いているのに 節季師走でも 節季師走でも お正月のように お正月のように 気楽に
ある	で と	遊んでいると 遊んでいると
てる	の	母の
いる	は でも に	僕は これでも 思ってるように
来る	へ	あとへ
出る	で に	朋友で 戦争に
する	て て て だり	以て来て 以て来て 出て 死んだり
ある	じゃ ね ものの が	遊んじゃいないやね—— 遊んじゃいないやね—— ものの 名前が
読む	を	名前を
なる	が	世の中が
つまる	に は て も	時には 時には 味気なくなって 人間も
云う	と	つまらないと
起る	が	気が
取る	しも	私しも
候う	に	年に
祝う	を	御雑煮を
ある	か と が	今度限りかと 今度限りかと 事が
しまう	が	なおのこと気が
来る	て て が	くさくさしてしまって くさくさしてしまって 東風が
思う	て んで と	書いてあるんで 書いてあるんで 好いと
来る	が	思ったが
なる	に	晩飯に
書く	から へ で も	なったから 母へ 返事でも 返事でも
思う	と	書こうと
かく	て と	思って ちょいと
ある	は も	手紙は 六尺以上も
出来る	が に は は	あるのだが 僕には 僕には 芸は
蒙る	でも で	いつ

下さる	は と	は 体重と
なる	に	御分りに
見合せる	を	顔を
分つ		
云う	は て と	主人は 見合せて 分ったと
云う	と	大抵と
作る	は が に	度合は 両人が 勝手に
知れる	から に は が	作ったのだから 場合には 場合には 応用が
よる	に	平均性理論に
立つ	と の が	よりますと 下のごとく 方程式が
云う	と は を	沢山だろうと 主人は 事を
見える	が と は に	首脳なんですがと 首脳なんですがと 寒月君は 気に
伺う	て	逐って
する	じゃ だけ は に	それじゃ 首脳だけは 首脳だけは 事に
られる	じゃ か と も に	しようじゃないかと しようじゃないかと しようじゃないかと 迷亭も 体に
しまう	を	式を
なる	て と が	略してしまうと 略してしまうと 力学的研究が
いる	は	遠慮は
略す	に が から	駄目になるのですが 駄目になるのですが いらんから
云う	と は で	略すさと 主人は 平気で
略す	が	無理ですが
叩く	と が で を と	よかろうと 迷亭が ところで 手を ぱちぱちと
移る	へ	英国へ
論じる	て	移って
申す	に と	中に ガルガと
見える	と が	論じますと 字が
れる	から	時代から
れる	から と	見えますから 違ないと
よる	に	説に
絞る		
られる	に	罪に
切れる	で	具合で
くべる	を	刑罰を
ある	が は として	罪人が 時は ものだとして
絞める	で も	兇漢でも 兇漢でも
云う	と	ないと
ある	と が が	よると ありますが 句が
知る	が か	どっちが 本当か
死ねる	と で	悪くすると 一度で
ある	が が に	知りませんが 事が 実例に
云う	と	フツ・ゼラルドと
絞める	を	悪漢を
ある	が	事が
飛び降りる	から	台から
しまう	で に は に が	はずみで 一度目には 一度目には ときに 縄が
過ぎる	が	縄が
着く	と は て が へ	やり直すと 今度は 長過ぎて 足が 地面へ
死ねる	ので	着いたので
手伝う	に が	三返目に 見物人が
さす	て	手伝って
話す	と	往生さしたと
くる	へ	ところへ
出る	と は と に が	やれやれと 迷亭は くると 急に 元気が
死ぬ		
浮かれ出す	な と まで	死に損いだなと 死に損いだなと 主人まで
ある	が	事

...

いる	に	御寺に
隔てる	と を	襖一と 重を
いる	て が	隔てて 尼が
云う	など と	尼などと 尼などと
見抜く	が を	尼が 性質を
見える	と	ものと
たたく	て を	見えて 鍋を
泣く		
笑う	ながら が	たたきながら 烏が
泣く		
笑う	が	烏が
取る	と を	笑ったと 拍子を
歌う	て	取って
なる	が が	主人が 尼が
云う	から と	時からだと 時からだと
笑う	たり	泣いたり
がる	たり	笑ったり
がる	たり	嬉しがったり
する	たり も	悲しがったり 人一倍も
続く	に も	代りに いずれも
云う		
転ずる	て が に	なくて 心機が むやみに
する	を に	これを 俗語に
云う	て	翻訳して
する	を	喧嘩を
起きる	ね	刎ね
かえる	が に を	主人が 急に 気を
読む	を	腸を
かかる	で て に	勢で かえて 読みに
云う	と	もっともと
なる	は ば	以上は 云わねば
とまる	に に	第一に 眼に
見る	を	上を
ある	と と	見ると 八日と
いる	も から を	韓国統監も 時代から 尻尾を
見える	て て と	追っ懸けてあるいていたと 追っ懸けてあるいていたと 追っ懸けてあるいていたと
いる	は を	時分は 何を
よむ	を に	ところを 無理に
ある	て と と と	していたんだろうと していたんだろうと よむと 大蔵卿と
する	か	逆か
見る	を	方を
なる	に	大蔵卿横に
いる	と は て を	見ると 今度は なって 昼寝を
続く	か で は	逆か 立ちでは 立ちでは
遣る		
見える	に で は と だけ	方に 木板で 汝はと 汝はと 二字だけ
見る	が	あとが
する		
おる	が て	見たいが 露出して
いる	に は だけ	行には 行には 二字だけ
読む	も	こいつも
構う	でも	ものでも
知れる	に	構わずに
云う	と	探偵と
受ける	を	教育を
挙げる	を	事実を
する	から に は	ないから ためには ためには
行く	に	始末に
もらう	を	遠慮を
する	を	遠慮を
させる		
する	に	事に
よる	に	ところに
もつ	を	虚構を
陥れる	て を に	もって 良民を 罪に
ある	と は さえ	よると 彼等は 事さえ
出す	が を	良民が 金を
おく	て	出して
する	が を に	者が 雇主を 罪に
くる	など 

刈り込む	ほど	ほど
かためる	で を に	刈り込んで 鼻を 真中に
いる	て に	かためて 方に
云う	と	これと
刈る	に	青坊主に
見える	て さえ	刈ってさえ 刈ってさえ
延ばす	の に	主人のように 主人のように
惹く	を	人目を
かぎる	に	顔に
出来る	て は	かぎって 学問は
知れる	は	事実は
見る		
分る	は の か か	着物は 書生のごとく 久留米がすりかまた 伊予絣か
られる	も と	ともかくも 絣と
着こなす	を か に	袷を 袖短かに 袖短かに
与える	が を	ものだそうだが 感じを
いる	に を まで	上に 親指を 三つまで
坐る	へ	上へ
いる	は て	彼は 坐って
かしこまる		
控える	が	ものが
する	に	気に
及ぶ	は に も	控えるのは するにも するにも
いる	が	乱暴者が
逢う	で に	途中で 先生に
する	て さえ を	逢ってさえ 逢ってさえ 礼を
する	を に	しないのを 自慢に
坐る	が でも に	連中が 三十分でも 人並に
得る	を	ところを
構える	て	生れ得て
かかわる	の	当人の
見る	に から	苦しいにかかわらず 傍から
かよう		
する	に を	かように 自己を
いる	で が を	運動場で ものが 力を
思う	て か と	具えているかと 具えているかと 具えているかと
ある	に も	憐れにも 憐れにも
やる		
なる	て ずつ に	やって 一人ずつ 相対に
なる	と	なると
いう		
ある	と ども に対して が	主人といえども 主人といえども 生徒に対して 重みが
れる	に	あるように
なす	って を	塵積って 山を
云う	と	なすと
する	も が	一生徒も 多勢が
なる	と と	聚合すると 団体と
知れる	から て を	云うから なって ストライキを
飲む	が を	臆病者が 酒を
なる	で	飲んで
頼む	を	衆を
騒ぎ出す	で	頼んで
酔っ払う	に	気に
取り落す	を	正気を
認める	と	ものと
差支える	て	認めて
ある	は	騒ぎ出すのは
恐れ入る	に	ばかように
云う	と	恐れ入ると
いる	より として に	云わんより 悄然として 襖に
云う	が と	薩摩絣が 老朽だと
つく	と の	先生と 名の
する	て に も を	云って 苟めにも 苟めにも 主人を
出来る	に	馬鹿に
押しやる	を	座布

行く		
入れる	こそ て て て を に	今晩こそ 出て行って 出て行って 兼て ヴァイオリンを 手に
いる	と で ばかり	入れようと 中で 事ばかり
つかう	を	偽病を
休む	て まで	つかって 学校まで
恐れ入る	と も	こりゃと 迷亭君も
いる	から を	中から 首を
たまる	て と が で	出していると 出していると 日暮れが 待遠で
もぐり込む	から から	ないから 頭から
眠る	を	眼を
見る	で て て	もぐり込んで 眠って 待って
出す	を	首を
する	が へ にあたって	日が 障子へ 一面にあたって
起る	と に は が	出すと するには するには 癇癪が
かたまる	に が	方に 影が
れる	て に	かたまって 秋風に
つく	が に	ゆすれるのが 眼に
云う	と	影と
剥く	を	皮を
おく	て へ	剥いて 軒へ
出る	を	床を
あける	を	障子を
出る	から て て へ	ないから 出て あけて 椽側へ
取る	を	甘干しを
食う	て て	出て 取って
聞く	かい と は を	うまかったかいと うまかったかいと 主人は 事を
わかる	など は	東京など あの味は
する	が	いいが
きく	と は が	したいと 今度は 東風君が
もぐる		
ふさぐ	て を	もぐって 眼を
暮れる	で が	ふさいで 日が
念じる	に に	ひそかに 神仏に
見る	ば が と て	暮れればいいがと 暮れればいいがと 暮れればいいがと 念じて
立つ	も	約三四時間も
思う	と	立ったと
出す	と を	よかろうと 首を
からむ	は	あには
照らす	を	障子を
する	は て	日は 照らして
かたまる	に が	方に 影が
する	と て	出すと かたまって
聞く		
返る		
ある	も	返も
出る	を	床を
あける	て を	出て 障子を
食う	て を	あけて 柿を
這入る	て へ	食ってまた 寝床へ
暮れる	て が	這入って 日が
こらす	ば と に に を	暮れればいいと 暮れればいいと ひそかに 神仏に 祈念を
く		
下さる	に	焦かずに
する	で	中で
出す	と を	よかろうと 首を
見る	て て	辛抱して 出して
かたまる	に が	方に 影が
いる	と は にあたって て	見ると 日は 一面にあたって かたまって
行く	まで	いつまで
出る	を	床を
開ける	て を	出て 

れる	から に	世間から なし崩しに
する	て	殺されて
付く	に	死に方に
する	を	名案を
する	て は が	して 趨勢は 自殺者が
もつ	を	方法を
去る	て を	もって この世を
なる	に	事に
なる		
云う	と	アーサージョーンスと
かく	の	人の
する	に を	なかに 自殺を
ある	が	哲学者が
する	に	事に
立つ	から も	今から 千年も
する		
云う	と	死と
する	より に	自殺より ほかに
なる	に は ば の に	後には 後には 云えば もののように もののように
なる	に	事に
なる	よ	なるよ
積む	も が	自殺も 大分研究が
なる	で に	積んで 科学に
なる	て で に を として	なって 中学校で 代りに 自殺学を 正科として
出る	な に	妙ですな 傍聴に
なる	に	迷亭先生御聞きに
なる	に	時分に
云う	と は	なると 先生は
云う	など と	諸君公徳などと 諸君公徳などと
なる	を	遺風を
する	として が に	青年として 諸君が 第一に
こす	に	好むところはこれを人に
なる	て	こして
する	を	自殺を
する	て に	展開して 他殺に
ござる	は て	ものは 生きて
見受ける	の に	大分苦痛のように 大分苦痛のように
殺す		
進ぜる	から て	るるから 殺して
違う	と	昔と
用いる	を	類を
なる	て は から を	違って 今日は 時節であるから 振舞を
あてこする		
なる	が	からかい殺すのが
なる	によって に も に も	技術によって 功徳にもなりまた 功徳にもなりまた 名誉にも 名誉にも
する	を	講義を
ある	が	事が
する	が を	警察が 生命財産を
いる	で は を と	現代では 現代では 保護するのを 目的と
なる	に	時分に
もつ	を	棍棒を
する	て を	もって 公民を
あるく	と て	なると 撲殺して
する	から で	大事だから 警察で
てる	は	国民は
くれる	から が に	苦痛だから 巡査が ために
利く	の	気の
しまう	は	ものは
れる	に	巡査に
限る	て から は か に	大概自殺してしまうから 大概自殺してしまうから 奴は 意気地なしか 不具者に
れる		
おく	は へ を	人間は 門口へ 張札を
ある	とか	男ありとか
くる	とか て ば が に	女ありとか はりつけてお

/Users/hidareimu/.pyenv/versions/anaconda3-4.4.0/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: generator 'neco_lines' raised StopIteration
  """Entry point for launching an IPython kernel.


## 47. 機能動詞構文のマイニング  (×)
動詞のヲ格にサ変接続名詞が入っている場合のみに着目したい．46のプログラムを以下の仕様を満たすように改変せよ．

「サ変接続名詞+を（助詞）」で構成される文節が動詞に係る場合のみを対象とする  
述語は「サ変接続名詞+を+動詞の基本形」とし，文節中に複数の動詞があるときは，最左の動詞を用いる  
述語に係る助詞（文節）が複数あるときは，すべての助詞をスペース区切りで辞書順に並べる  
述語に係る文節が複数ある場合は，すべての項をスペース区切りで並べる（助詞の並び順と揃えよ）  
例えば「別段くるにも及ばんさと、主人は手紙に返事をする。」という文から，以下の出力が得られるはずである．  

返事をする      と に は        及ばんさと 手紙に 主人は  


このプログラムの出力をファイルに保存し，以下の事項をUNIXコマンドを用いて確認せよ．  
コーパス中で頻出する述語（サ変接続名詞+を+動詞）  
コーパス中で頻出する述語と助詞パターン  



In [100]:
for i, chunks in enumerate(neco_lines(), 1):
    for j, chunk in enumerate(chunks):
        if chunk.srcs != []:
            if "動詞" in [morph.pos for morph in chunk.morphs]:
                verb_chunk = chunk.print_chunk()    
                    
                for src in chunk.srcs:
                    particle_candi = []
                    chunk_candi = []
                    _surface =  [morph.surface for morph in chunks[src].morphs]
                    _pos1 = [morph.pos1 for morph in chunks[src].morphs]
                    if "を" in _surface and "サ変接続" in _pos1:
                        particle_candi.append(chunks[src].morphs[_surface.index("を")].surface)
                        chunk_candi.append(chunks[src].print_chunk())
                        print(verb_chunk +"\t"+ " ".join(particle_candi)+"\t"+" ".join(chunk_candi))            


                            

して	を	決心を
してやってから	を	返報を
している	を	昼寝を
する	を	昼寝を
加える	を	迫害を
するには	を	家族的生活を
しよう	を	話を
したり	を	投書を
しているのを	を	話を
したら	を	写生を
していたら	を	昼寝を
禁じ得なかった	を	失笑するのを
見ると	を	彩色を
した	を	欠伸を
した	を	報道を
しないと	を	挨拶を
食ってるらしい	を	御馳走を
して	を	問答を
していると	を	雑談を
繰り返した	を	自慢話しを
する	を	自慢を
飲み込んだから	を	呼吸を
定めた	を	思案を
あるく	を	御馳走を
食うよりも	を	御馳走を
した	を	大分放蕩を
したと	を	放蕩を
するべく	を	放蕩を
いう	を	元来放蕩家を
する	を	放蕩を
力めているが	を	写生を
すると	を	写生を
主張した	を	写生を
聞いて	を	対話を
した	を	半分降参を
惹いたのは	を	注意を
した	を	苦心を
している	を	勉強を
認められなかった	を	存在を
聞いて	を	談話を
しました	を	御無沙汰を
やりましてねと	を	合奏会を
して	を	勘定を
通る	を	往来を
する	を	返事を
した	を	決心を
するという	を	間食を
受けつつあると	を	仕付を
すると	を	我儘を
する	を	返事を
求めつつあるのか	を	慰安を
しているようだ	を	喧嘩を
断てと	を	是非香の物を
愛していた	を	按摩術を
うけたと	を	治療を
顛倒しなければ	を	位置を
食うなと	を	是非固形体を
した	を	議論を
して	を	弁解を
した	を	挨拶を
始めるなどというのは	を	晩酌を
する	を	遠征を
つける	を	始末を
予知す	を	適不適を
食べかけて	を	御馳走を
した	を	失敗を
する	を	話を
する	を	挨拶を
している	を	返事を
した	を	返事を
した	を	降参を
している	を	欠伸を
して	を	挨拶を
する	を	合図を
なさる	を	形容を
表して	を	同情を
読む	を	通信を
しないんです	を	返事を
表する	を	同情を
組織しまして	を	朗読会というのを
続けたいつもりで	を	研究を
やりました	を	心中物を
持って	を	同情を
呈出した	を	質問を
仰ぎたいので	を	御尽力を
願いたいのでと	を	御捺印を
致さんと	を	御馳走を
する	を	返事を
尽したる	を	研究

した	を	いたずらを
買いながら	を	喧嘩を
張れるだけ	を	我儘を
払ったりする	を	下宿料を
払えばこそ	を	尊敬を
執行するのは	を	結婚を
洗錬するのは	を	同情を
主張する	を	非結婚論を
かき散らしたのだね	を	乱暴を
した	を	修行を
起して	を	神経衰弱を
した	を	返事を
する	を	返事を
願いましょう	を	是非周旋を
乱す	を	算を
する	を	対面を
すると	を	油断を
重ねて	を	我慢を
使う	を	行水を
使えば	を	行水を
使おうなどとは	を	行水を


/Users/hidareimu/.pyenv/versions/anaconda3-4.4.0/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: generator 'neco_lines' raised StopIteration
  """Entry point for launching an IPython kernel.


## 48. 名詞から根へのパスの抽出  
文中のすべての名詞を含む文節に対し，その文節から構文木の根に至るパスを抽出せよ． ただし，構文木上のパスは以下の仕様を満たすものとする．

各文節は（表層形の）形態素列で表現する  
パスの開始文節から終了文節に至るまで，各文節の表現を"->"で連結する  
「吾輩はここで始めて人間というものを見た」という文（neko.txt.cabochaの8文目）から，次のような出力が得られるはずである．  

吾輩は -> 見た
ここで -> 始めて -> 人間という -> ものを -> 見た
人間という -> ものを -> 見た
ものを -> 見た

In [110]:
for i, chunks in enumerate(neco_lines(), 1):
    for j, chunk in enumerate(chunks):
        if chunk.dst != -1 and "名詞" in chunk.pos_list():
            path = [ ]
            now_chunk = chunk
            while True:
                path.append(now_chunk.print_chunk())
                if now_chunk.dst == -1:
                    break
                now_chunk = chunks[now_chunk.dst]
                
                
            if len(path)>1:
                print("->".join(path))

                            

吾輩は->猫である
名前は->無い
どこで->生れたか->つかぬ
見当が->つかぬ
何でも->薄暗い->所で->泣いて->記憶している
所で->泣いて->記憶している
ニャーニャー->泣いて->記憶している
いた事だけは->記憶している
吾輩は->見た
ここで->始めて->人間という->ものを->見た
人間という->ものを->見た
ものを->見た
あとで->聞くと->種族であったそうだ
それは->種族であったそうだ
書生という->人間中で->種族であったそうだ
人間中で->種族であったそうだ
一番->獰悪な->種族であったそうだ
獰悪な->種族であったそうだ
書生というのは->話である
我々を->捕えて->煮て->食うという->話である
当時は->なかったから->思わなかった
何という->考も->なかったから->思わなかった
考も->なかったから->思わなかった
彼の->掌に->載せられて->持ち上げられた->時->フワフワした->感じが->あったばかりである
掌に->載せられて->持ち上げられた->時->フワフワした->感じが->あったばかりである
スーと->持ち上げられた->時->フワフワした->感じが->あったばかりである
時->フワフワした->感じが->あったばかりである
感じが->あったばかりである
掌の->上で->落ちついて->見たのが->人間という->ものの->見始であろう
上で->落ちついて->見たのが->人間という->ものの->見始であろう
書生の->顔を->見たのが->人間という->ものの->見始であろう
顔を->見たのが->人間という->ものの->見始であろう
見たのが->人間という->ものの->見始であろう
人間という->ものの->見始であろう
ものの->見始であろう
時->ものだと->思った->感じが->残っている
妙な->ものだと->思った->感じが->残っている
ものだと->思った->感じが->残っている
感じが->残っている
今でも->残っている
第一毛をもって->装飾されべきはずの->顔が->つるつるして->薬缶だ
装飾されべきはずの->顔が->つるつるして->薬缶だ
顔が->つるつるして->薬缶だ
その後->逢ったが->ない
猫にも->逢ったが->ない
片輪には->ない
一度も->出会わした->事が->ない
事が->ない
顔の->

犬をも->挫し->籠っているので->抱いた
挫し->籠っているので->抱いた
ぐべき力が->籠っているので->抱いた
吾輩は->抱いた
恐れを->抱いた
挨拶を->しないと->険呑だと->思ったから->猫である
険呑だと->思ったから->猫である
吾輩は->猫である
名前は->ないと->装って->答えた
平気を->装って->答えた
冷然と->答えた
時->おった
吾輩の->心臓は->おった
心臓は->おった
平時よりも->烈しく->鼓動して->おった
鼓動して->おった
彼は->猫だ
大に->軽蔑せる->調子で->猫だ
軽蔑せる->調子で->猫だ
調子で->猫だ
何->猫だ
猫が->聞いて->あ
あきれら->あ
全てえ->住んでるんだ->傍若無人である
どこに->住んでるんだ->傍若無人である
住んでるんだ->傍若無人である
吾輩は->いるのだ->事だろうと->思った
ここの->教師の->家に->いるのだ->事だろうと->思った
教師の->家に->いるのだ->事だろうと->思った
家に->いるのだ->事だろうと->思った
いるのだ->事だろうと->思った
事だろうと->思った
いやに->瘠せてるじゃねえかと->吹きかける
大王だけに->吹きかける
気焔を->吹きかける
言葉付から->察すると->思われない
察すると->思われない
良家の->猫とも->思われない
猫とも->思われない
膏->切って->肥満している->ところを->見ると->食ってるらしい->暮しているらしい
肥満している->ところを->見ると->食ってるらしい->暮しているらしい
ところを->見ると->食ってるらしい->暮しているらしい
御馳走を->食ってるらしい->暮しているらしい
豊かに->暮しているらしい
吾輩は->聞かざるを得なかった
云う君は->誰だいと->聞かざるを得なかった
誰だいと->聞かざるを得なかった
己れあ->黒よ昂然たる->ものだ
車屋の->黒よ昂然たる->ものだ
黒よ昂然たる->ものだ
車屋の->黒は->乱暴猫である
黒は->乱暴猫である
近辺で->知らぬ->者->乱暴猫である
者->乱暴猫である
車屋だけに->強いばかりで->ないから->交際しない
教育が->ないから->交際しない
誰も->交際しない
同盟敬遠主義の->的に->なっている->奴だ
的に->なっている->奴だ


猫じゃを->躍っている
その上に->認められてある
日本の->墨で->かいて->認められてある
墨で->かいて->認められてある
吾輩は->猫であると->黒と->かいて->認められてある
猫であると->黒と->かいて->認められてある
黒と->かいて->認められてある
右の->側に->読むや->認められてある
側に->読むや->認められてある
書を->読むや->認められてある
猫の->春一日という->俳句さえ->認められてある
春一日という->俳句さえ->認められてある
俳句さえ->認められてある
これは->来たので->見たって->一見して->わかるはずであるのに->悟らないと->見えて->捻って->言った
主人の->旧門下生より->来たので->見たって->一見して->わかるはずであるのに->悟らないと->見えて->捻って->言った
旧門下生より->来たので->見たって->一見して->わかるはずであるのに->悟らないと->見えて->捻って->言った
誰が->見たって->一見して->わかるはずであるのに->悟らないと->見えて->捻って->言った
一見して->わかるはずであるのに->悟らないと->見えて->捻って->言った
意味が->わかるはずであるのに->悟らないと->見えて->捻って->言った
わかるはずであるのに->悟らないと->見えて->捻って->言った
濶な->主人は->悟らないと->見えて->捻って->言った
主人は->悟らないと->見えて->捻って->言った
不思議そうに->捻って->言った
首を->捻って->言った
今年は->言った
猫の->年かなと->言った
年かなと->言った
独言を->言った
吾輩が->有名になったのを->着かずに->いると->見える
これほど->有名になったのを->着かずに->いると->見える
有名になったのを->着かずに->いると->見える
気が->着かずに->いると->見える
ところへ->持ってくる
下女が->持ってくる
第三の->端書を->持ってくる
端書を->持ってくる
今度は->絵端書ではない
恭賀新年と->かいて->ある
傍らに->ある
乍恐縮かの->猫へも->ある
猫へも->ある
御伝声->奉->願上候と->ある
願上候と->ある
迂遠な->主人でも->あれば->分る->ものと->見えて->付いたように->見た
主

いやな->猫ねえと->仰せられる
猫ねえと->仰せられる
主人さえ->出て来て->いった
書斎から->出て来て->いった
馬鹿野郎と->いった
云うのは->小供ばかりである
みんな->申し合せたように->笑っている
申し合せたように->笑っている
腹は->立つ->苦しくはある->弱った
踊は->弱った
訳に->ゆかぬ->弱った
笑いが->やみそうになったら->なる->女の子が->いったので->笑われた
やみそうになったら->なる->女の子が->いったので->笑われた
五つに->なる->女の子が->いったので->笑われた
女の子が->いったので->笑われた
様->随分ねと->いったので->笑われた
猫も->随分ねと->いったので->笑われた
狂瀾を->するという->勢でまた->笑われた
既倒に->するという->勢でまた->笑われた
勢でまた->笑われた
大変->笑われた
人間の->同情に->乏しい->実行も->大分見聞したが->なかった
同情に->乏しい->実行も->大分見聞したが->なかった
実行も->大分見聞したが->なかった
大分見聞したが->なかった
時->感じた->事は->なかった
事は->なかった
天祐も->消え失せて->なって->白黒するの->醜態を->演ずるまでに->閉口した
どっかへ->消え失せて->なって->白黒するの->醜態を->演ずるまでに->閉口した
在来の->通り四つ這に->なって->白黒するの->醜態を->演ずるまでに->閉口した
通り四つ這に->なって->白黒するの->醜態を->演ずるまでに->閉口した
眼を->白黒するの->醜態を->演ずるまでに->閉口した
白黒するの->醜態を->演ずるまでに->閉口した
醜態を->演ずるまでに->閉口した
見殺しに->するのも->気の毒と->見えて->命ずる
するのも->気の毒と->見えて->命ずる
気の毒と->見えて->命ずる
餅を->とってやれと->命ずる
主人が->命ずる
御三に->命ずる
御三は->見る
眼付で->見る
細君を->見る
細君は->見たいが->だまっている
踊は->見たいが->だまっている
気は->ないので->だまっている
主人は->顧みる
下女を->顧みる
御三は->引く
御馳走を->食べかけて->起された->時のように->引く
半分->食べかけて->起された->時のように

上へ->落ちる
東風子は->頬張る
菓子皿の->中の->カステラを->つまんで->頬張る
中の->カステラを->つまんで->頬張る
カステラを->つまんで->頬張る
一口に->頬張る
吾輩は->思い出す
今朝の->雑煮事件を->思い出す
雑煮事件を->思い出す
主人が->出て来た->時は->時であった
書斎から->持って->出て来た->時は->時であった
印形を->持って->出て来た->時は->時であった
時は->時であった
東風子の->胃の->中に->落ちついた->時であった
胃の->中に->落ちついた->時であった
中に->落ちついた->時であった
カステラが->落ちついた->時であった
主人は->着かぬらしい
菓子皿の->カステラが->足りなくなった->事には->着かぬらしい
カステラが->足りなくなった->事には->着かぬらしい
一切->足りなくなった->事には->着かぬらしい
事には->着かぬらしい
気が->着かぬらしい
気が->つくと->すれば->疑われる->ものは->吾輩であろう
第一に->疑われる->ものは->吾輩であろう
ものは->吾輩であろう
東風子が->帰ってから->見ると->来ている
主人が->入って->見ると->来ている
書斎に->入って->見ると->来ている
机の->上を->見ると->来ている
上を->見ると->来ている
迷亭先生の->手紙が->来ている
手紙が->来ている
新年の->御慶->目出度->申納候
御慶->目出度->申納候
いつに->なく->真面目だと->思う
出が->真面目だと->思う
真面目だと->思う
主人が->思う
迷亭先生の->手紙に->真面目なのは->ないので->くらいである
手紙に->真面目なのは->ないので->くらいである
真面目なのは->ないので->くらいである
この間などは->云うのが->来た->くらいである
其後別に->着せる->婦人も->参らず->乍憚御休心可被下候と->云うのが->来た->くらいである
恋->着せる->婦人も->参らず->乍憚御休心可被下候と->云うのが->来た->くらいである
婦人も->参らず->乍憚御休心可被下候と->云うのが->来た->くらいである
無之->参らず->乍憚御休心可被下候と->云うのが->来た->くらいである
方より->参らず->乍憚御休心可被下候と->云うのが->

...

迷亭先生今度は->下した
関係の->ない->方面へ->下した
方面へ->下した
一石を->下した
床の間の->前で->争っていると->坐っている
前で->争っていると->坐っている
迷亭君と->独仙君が->争っていると->坐っている
独仙君が->争っていると->坐っている
一生懸命に->争っていると->坐っている
輸贏を->争っていると->坐っている
座敷の->入口には->坐っている
入口には->坐っている
寒月君と->東風君が->相ならんで->坐っている
東風君が->相ならんで->坐っている
相ならんで->坐っている
傍に->して->坐っている
主人が->して->坐っている
顔を->して->坐っている
寒月君の->前に->排列してあるのは->奇観である
前に->排列してあるのは->奇観である
鰹節が->三本->排列してあるのは->奇観である
三本->排列してあるのは->奇観である
裸の->まま->排列してあるのは->奇観である
まま->排列してあるのは->奇観である
畳の->上に->排列してあるのは->奇観である
上に->排列してあるのは->奇観である
行儀->よく->排列してあるのは->奇観である
排列してあるのは->奇観である
鰹節の->出処は->ぬくもっていた
出処は->ぬくもっていた
寒月君の->懐で->取り出した->時は->ぬくもっていた
懐で->取り出した->時は->ぬくもっていた
時は->ぬくもっていた
暖->たかく->ぬくもっていた
手のひらに->感じた->くらい->ぬくもっていた
裸ながら->ぬくもっていた
主人と->東風君は->注いでいると->開いた
東風君は->注いでいると->開いた
妙な->眼を->して->注いでいると->開いた
眼を->して->注いでいると->開いた
視線を->注いでいると->開いた
鰹節の->上に->注いでいると->開いた
上に->注いでいると->開いた
寒月君は->開いた
口を->開いた
四日ばかり前に->帰って来たのですが->ものですから->上がられなかったのです
国から->帰って来たのですが->ものですから->上がられなかったのです
帰って来たのですが->ものですから->上がられなかったのです
用事が->あって->あるいていた->ものですから->上がられなかったのです
方々馳け->あるいていた->ものですから->上

枯柳の->数を->勘定して->計算して->ふかして->見た
数を->勘定して->計算して->ふかして->見た
勘定して->計算して->ふかして->見た
病院の->横で->計算して->ふかして->見た
横で->計算して->ふかして->見た
窓の->灯を->計算して->ふかして->見た
灯を->計算して->ふかして->見た
計算して->ふかして->見た
紺屋橋の->上で->ふかして->見た
上で->ふかして->見た
巻煙草を->ふかして->見た
二本->ふかして->見た
時計を->見た
十時に->なったかい
事に->ならないね
——紺屋橋を->渡り切って->上って行くと->あった
川添に->上って行くと->あった
東へ->上って行くと->あった
按摩に->あった
三人->あった
犬が->吠えましたよ先生
秋の->夜長に->きくのは->芝居がかりだね
夜長に->きくのは->芝居がかりだね
川端で->きくのは->芝居がかりだね
犬の->吠を->きくのは->芝居がかりだね
吠を->きくのは->芝居がかりだね
きくのは->芝居がかりだね
君は->格だ
落人と->云う->格だ
何か->事でもしたんですか
可哀相に->買うのが->事じゃ->罪人ですよ
ヴァイオリンを->買うのが->事じゃ->罪人ですよ
買うのが->事じゃ->罪人ですよ
事じゃ->罪人ですよ
音楽学校の->生徒は->罪人ですよ
生徒は->罪人ですよ
みんな->罪人ですよ
人が->認めない->事を->すれば->ない
事を->すれば->ない
事を->しても->ない
罪人さ->ない
世の中に->ならない->ものは->ない
罪人ほど->ならない->ものは->ない
あてに->ならない->ものは->ない
ものは->ない
耶蘇も->生れれば->罪人さ
世に->生れれば->罪人さ
好男子寒月君も->罪人さ
所で->買えば->罪人さ
ヴァイオリンを->買えば->罪人さ
それじゃ->負けて->しておきましょう
罪人と->しておきましょう
罪人は->いいですが->弱りました
十時に->ならないのには->弱りました
ならないのには->弱りました
一->返->勘定するさ
町の->名を->勘定するさ
名を->勘定するさ
それで->足りなければまた->かんかんさせるさ
秋の->日を->かんかんさせるさ
日を->かんかんさせるさ
甘干しの->渋柿を

侍従や->官女が->笑い出した——->出したのではない->出そうと->したのさ->云うんだが->もんだ
官女が->笑い出した——->出したのではない->出そうと->したのさ->云うんだが->もんだ
みんな->笑い出した——->出したのではない->出そうと->したのさ->云うんだが->もんだ
笑い出した——->出したのではない->出そうと->したのさ->云うんだが->もんだ
出したのではない->出そうと->したのさ->云うんだが->もんだ
出そうと->したのさ->云うんだが->もんだ
したのさ->云うんだが->もんだ
女皇が->向いて->したら->かけて->云うんだが->もんだ
後ろを->向いて->したら->かけて->云うんだが->もんだ
何か->したら->かけて->云うんだが->もんだ
相図を->したら->かけて->云うんだが->もんだ
多勢の->侍従官女が->かけて->云うんだが->もんだ
侍従官女が->かけて->云うんだが->もんだ
みんな->かけて->云うんだが->もんだ
椅子へ->かけて->云うんだが->もんだ
腰を->かけて->云うんだが->もんだ
カーライルは->失わなかったと->云うんだが->もんだ
面目を->失わなかったと->云うんだが->もんだ
云うんだが->もんだ
御念の->入った->親切も->あった->もんだ
親切も->あった->もんだ
カーライルの->事なら->知れませんよと->試みた
事なら->知れませんよと->試みた
みんなが->立ってても->知れませんよと->試みた
平気だったかも->知れませんよと->試みた
寒月君が->試みた
短評を->試みた
親切の->方の->自覚心は->いいがねと->進行する
方の->自覚心は->いいがねと->進行する
自覚心は->いいがねと->進行する
独仙君は->進行する
自覚心が->あるだけ->するにも->折れる->訳に->なる
親切を->するにも->折れる->訳に->なる
骨が->折れる->訳に->なる
訳に->なる
気の毒な->事さ
文明が->進むに従って->なくなる->交際が->おだやかになるなどと->云うが->大間違いさ
殺伐の->気が->なくなる->交際が->おだやかになるなどと->云うが->大間違いさ
気が->なくなる->交際が->おだやかになるなどと->云うが->大間違いさ
個人と->個人の-

乱暴に->あいて->あらわれた
多々良三平君の->顔が->あらわれた
顔が->あらわれた
その間から->あらわれた
三平君->今日は->似ず->着て->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
今日は->似ず->着て->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
いつに->似ず->着て->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
真白な->シャツに->着て->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
シャツに->着て->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
卸立ての->フロックを->着て->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
フロックを->着て->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
幾分か->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
相場を->狂わせてる->上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
上へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
右の->手へ->下げた->四本の->麦酒を->置くと同時に->せず->下ろしてかつ->崩したのは->振である
手へ->下げた->四本の->麦酒を->置くと同時に->せず->下ろしてかつ->崩したのは->振である
重そうに->下げた->四本の->麦酒を->置くと同時に->せず->下ろしてかつ->崩したのは->振である
四本の->麦酒を->置くと同時に->せず->下ろしてかつ->崩したのは->振である
麦酒を->置くと同時に->せず->下ろしてかつ->崩したのは->振である
縄ぐるみ->鰹節の->傍へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
鰹節の->傍へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
傍へ->置くと同時に->せず->下ろしてかつ->崩したのは->振である
挨拶も->せず->下ろしてかつ->崩したのは->振である
腰を->下ろしてかつ->崩したのは->振で

/Users/hidareimu/.pyenv/versions/anaconda3-4.4.0/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: generator 'neco_lines' raised StopIteration
  """Entry point for launching an IPython kernel.


## 49. 名詞間の係り受けパスの抽出  
文中のすべての名詞句のペアを結ぶ最短係り受けパスを抽出せよ．  
ただし，名詞句ペアの文節番号がiとj（i<j）のとき，係り受けパスは以下の仕様を満たすものとする．

問題48と同様に，パスは開始文節から終了文節に至るまでの各文節の表現（表層形の形態素列）を"->"で連結して表現する。  
文節iとjに含まれる名詞句はそれぞれ，XとYに置換する。
また，係り受けパスの形状は，以下の2通りが考えられる。

・文節iから構文木の根に至る経路上に文節jが存在する場合:  
    文節iから文節jのパスを表示

・上記以外で，文節iと文節jから構文木の根に至る経路上で共通の文節kで交わる場合:   
    文節iから文節kに至る直前のパスと文節jから文節kに至る直前までのパス，文節kの内容を"|"で連結して表示  
    
    
例えば，「吾輩はここで始めて人間というものを見た。」という文（neko.txt.cabochaの8文目）から，次のような出力が得られるはずである．  
    Xは | Yで -> 始めて -> 人間という -> ものを | 見た  
    Xは | Yという -> ものを | 見た  
    Xは | Yを | 見た  
    Xで -> 始めて -> Y  
    Xで -> 始めて -> 人間という -> Y  
    Xという -> Y  


In [143]:
import itertools
for chunks in (neco_lines()):
    print("0")
    index_noun = [i for i in range(len(chunks))
                  if "名詞" in chunks[i].pos_list()]
    index_noun_pair = list(itertools.combinations(index_noun,2))
    
    #checker
    conflict_y = False
    conflict_pos = -1
    x_path = set()
    
    for x,y in index_noun_pair:
        #x -> root
        dst = chunks[x].dst
        while dst!=-1:
            if dst == y:
                conflict_y =True
                break
            x_path.add(dst)
            dst = chunks[dst].dst
            
        #y -> root
        if conflict_y == False:
            dst = chunks[y].dst
            while dst!=-1:
                if dst in x_path:
                    conflict_pos = dst
                    break
                else:
                    dst = chunks[dst].dst
        
        if conflict_pos == -1:
            #XからYに衝突
            tmp = "X"
            dst = chunks[x].dst
            while dst != -1:
                if dst == y:
                    tmp += "->" + "Y"
                else:
                    tmp += "->" + chunks[dst].print_chunk()
                dst = chunks[dst].dst
            print(tmp)
        
        else:
            tmp = "X"
            
            dst = chunks[x].dst
            while dst != conflict_pos:
                tmp += "->" + chunks[dst].print_chunk()
                dst = chunks[dst].dst
            
            tmp += "|"
            
            tmp += "Y"
            
            dst = chunks[y].dst
            while dst != conflict_pos:
                tmp += "->" + chunks[dst].print_chunk()
                dst = chunks[dst].dst
            
            tmp += "|"
            tmp += chunks[conflict_pos].print_chunk()
            print(tmp)
            
            

0
0
0
X->Y
0
0
0
X->生れたか|Y|つかぬ
0
X->薄暗い->Y->泣いて->記憶している
X->薄暗い->所で->泣いて->記憶している
X->薄暗い->所で->泣いて->記憶している
X->薄暗い->所で->泣いて->Y
X->泣いて->記憶している
X->泣いて->記憶している
X->泣いて->Y
X->泣いて->記憶している
X->泣いて->Y
X->Y
0
X|Y->始めて->人間という->ものを|見た
X|Y->ものを|見た
X|Y|見た
X->始めて->人間という->ものを|Y->ものを|見た
X->始めて->人間という->ものを|Y|見た
X->ものを|Y|見た
0
X->聞くと|Y|種族であったそうだ
X->聞くと|Y->人間中で|種族であったそうだ
X->聞くと|Y|種族であったそうだ
X->聞くと|Y->獰悪な|種族であったそうだ
X->聞くと|Y|種族であったそうだ


KeyboardInterrupt: 

In [140]:
index_noun

[1, 2, 3, 5, 6]